## Data Loading

In [1]:
import streamlit as st
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from pathlib import Path
from typing import List, Dict, Tuple
import warnings
warnings.filterwarnings('ignore')

# Import custom modules
from new_script.data_reader import GTExDataReader
from new_script.preprocessing import DataPreprocessor
from new_script.network_analysis import NetworkAnalysis
from new_script.mdc_analysis import MDCAnalyzer
from new_script.visualization import NetworkVisualizer

In [2]:
reader = GTExDataReader()
expression_df, gene_metadata = reader.read_gct_file(
                "GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_tpm.gct"
            )

Found data directory: /Users/edeneldar/CoExpression_reProduction/data
Reading GCT file: data/GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_tpm.gct
GCT version: #1.2
Dimensions: 56200 genes, 17382 samples
Preparing to read 17382 samples
Processed 1000/56200 genes (1.8%)...
Processed 2000/56200 genes (3.6%)...
Processed 3000/56200 genes (5.3%)...
Processed 4000/56200 genes (7.1%)...
Processed 5000/56200 genes (8.9%)...
Processed 6000/56200 genes (10.7%)...
Processed 7000/56200 genes (12.5%)...
Processed 8000/56200 genes (14.2%)...
Processed 9000/56200 genes (16.0%)...
Processed 10000/56200 genes (17.8%)...
Processed 11000/56200 genes (19.6%)...
Processed 12000/56200 genes (21.4%)...
Processed 13000/56200 genes (23.1%)...
Processed 14000/56200 genes (24.9%)...
Processed 15000/56200 genes (26.7%)...
Processed 16000/56200 genes (28.5%)...
Processed 17000/56200 genes (30.2%)...
Processed 18000/56200 genes (32.0%)...
Processed 19000/56200 genes (33.8%)...
Processed 20000/56200 genes (35.6%).

In [3]:
sample_attrs = reader.read_sample_attributes()
subject_attrs = reader.read_subject_phenotypes()
protein_coding = reader.read_protein_coding_genes()



Reading sample attributes: data/GTEx_Analysis_v8_Annotations_SampleAttributesDS.tsv
Loaded sample attributes: (22951, 62)
Reading subject phenotypes: data/GTEx_Analysis_v8_Annotations_SubjectPhenotypesDS.tsv
Loaded subject phenotypes: (980, 3)
Reading HGNC data: data/hgnc_complete_set.tsv
Found 19293 protein coding genes


In [4]:
available_tissues = reader.get_available_tissues(sample_attrs)
print(f"Available tissues: {available_tissues}")
loaded_samples = set(expression_df.columns)
tissues_with_samples = []
tissue_sample_counts = {}

for tissue in available_tissues:
    all_tissue_samples = reader.get_tissue_samples(sample_attrs, tissue)
    loaded_tissue_samples = [s for s in all_tissue_samples if s in loaded_samples]
    if len(loaded_tissue_samples) >= 10:
        tissues_with_samples.append(tissue)
        tissue_sample_counts[tissue] = len(loaded_tissue_samples)

tissues_with_samples.sort(key=lambda x: tissue_sample_counts[x], reverse=True)

if not tissues_with_samples:
    print("No tissues have sufficient samples in the loaded data.")

Available tissues: ['Adipose - Subcutaneous', 'Adipose - Visceral (Omentum)', 'Adrenal Gland', 'Artery - Aorta', 'Artery - Coronary', 'Artery - Tibial', 'Bladder', 'Brain - Amygdala', 'Brain - Anterior cingulate cortex (BA24)', 'Brain - Caudate (basal ganglia)', 'Brain - Cerebellar Hemisphere', 'Brain - Cerebellum', 'Brain - Cortex', 'Brain - Frontal Cortex (BA9)', 'Brain - Hippocampus', 'Brain - Hypothalamus', 'Brain - Nucleus accumbens (basal ganglia)', 'Brain - Putamen (basal ganglia)', 'Brain - Spinal cord (cervical c-1)', 'Brain - Substantia nigra', 'Breast - Mammary Tissue', 'Cells - Cultured fibroblasts', 'Cells - EBV-transformed lymphocytes', 'Cells - Leukemia cell line (CML)', 'Cervix - Ectocervix', 'Cervix - Endocervix', 'Colon - Sigmoid', 'Colon - Transverse', 'Esophagus - Gastroesophageal Junction', 'Esophagus - Mucosa', 'Esophagus - Muscularis', 'Fallopian Tube', 'Heart - Atrial Appendage', 'Heart - Left Ventricle', 'Kidney - Cortex', 'Kidney - Medulla', 'Liver', 'Lung', '

In [26]:
tissues = ['Muscle - Skeletal',
     'Whole Blood',
     'Skin - Sun Exposed (Lower leg)',
     'Skin - Not Sun Exposed (Suprapubic)',
     'Adipose - Subcutaneous',
     'Thyroid',
     'Artery - Tibial',
     'Nerve - Tibial',
     'Lung',
     'Brain - Cerebellum',
     'Heart - Atrial Appendage',
     'Brain - Cortex',
     'Adipose - Visceral (Omentum)']

In [28]:
tissue_samples = {}
groups = ['young', 'old']

for tissue in tissues:
    tissue_samples[tissue] = {}
    for group in groups:
        tissue_samples[tissue][group] = reader.filter_samples_by_metadata(
            sample_attrs, 
            subject_attrs,
            tissue = tissue, 
            age_group = group, 
            min_rin = 5.6
        )


After RIN >= 5.6: 19828 samples
After tissue filter (Muscle - Skeletal): 1019 samples
   Extracted 1019 subject IDs from 1019 samples
   Samples with valid subject IDs: 1019
   Samples with phenotype data: 1019
After age group filter (young): 653 samples
After RIN >= 5.6: 19828 samples
After tissue filter (Muscle - Skeletal): 1019 samples
   Extracted 1019 subject IDs from 1019 samples
   Samples with valid subject IDs: 1019
   Samples with phenotype data: 1019
After age group filter (old): 366 samples
After RIN >= 5.6: 19828 samples
After tissue filter (Whole Blood): 929 samples
   Extracted 929 subject IDs from 929 samples
   Samples with valid subject IDs: 929
   Samples with phenotype data: 929
After age group filter (young): 612 samples
After RIN >= 5.6: 19828 samples
After tissue filter (Whole Blood): 929 samples
   Extracted 929 subject IDs from 929 samples
   Samples with valid subject IDs: 929
   Samples with phenotype data: 929
After age group filter (old): 317 samples
After 

In [30]:
# Save the filtered samples for later use
available_samples = set(expression_df.columns)
for tissue, groups in tissue_samples.items():
    for group, samples in groups.items():
        path = Path(f"filtered_samples/{tissue.replace(' ', '_')}_{group}.csv")
        path.parent.mkdir(parents=True, exist_ok=True)
        pd.Series(samples).to_csv(path, index=False)


In [19]:
# Check what samples we actually have in the expression data
available_samples = set(expression_df.columns)
print(f"Total samples in expression data: {len(available_samples)}")

# Check how many of the muscle samples are actually in our data
young_muscle_available = [s for s in young_muscle_samples_filtered if s in available_samples]
old_muscle_available = [s for s in old_muscle_samples_filtered if s in available_samples]

print(f"Young muscle samples found: {len(young_muscle_samples_filtered)}")
print(f"Young muscle samples available in data: {len(young_muscle_available)}")
print(f"Old muscle samples found: {len(old_muscle_samples_filtered)}")
print(f"Old muscle samples available in data: {len(old_muscle_available)}")

# Use only the available samples
all_muscle_samples = young_muscle_available + old_muscle_available
print(f"Total muscle samples we can use: {len(all_muscle_samples)}")

Total samples in expression data: 17382
Young muscle samples found: 653
Young muscle samples available in data: 510
Old muscle samples found: 366
Old muscle samples available in data: 292
Total muscle samples we can use: 802


In [20]:
# Use only samples that are actually available in our expression data
available_samples = set(expression_df.columns)
young_muscle_available = [s for s in young_muscle_samples_filtered if s in available_samples]
old_muscle_available = [s for s in old_muscle_samples_filtered if s in available_samples]
all_muscle_samples = young_muscle_available + old_muscle_available

print(f"Using {len(all_muscle_samples)} muscle samples ({len(young_muscle_available)} young, {len(old_muscle_available)} old)")

preprocessor = DataPreprocessor()

Using 802 muscle samples (510 young, 292 old)


In [18]:
expression_df[all_muscle_samples[0]]

ENSG00000223972.5        0.000
ENSG00000227232.5        1.036
ENSG00000278267.1        0.000
ENSG00000243485.5        0.000
ENSG00000237613.2        0.000
                       ...    
ENSG00000198695.2    17820.000
ENSG00000210194.1       59.830
ENSG00000198727.2    33600.000
ENSG00000210195.2        1.042
ENSG00000210196.2        2.024
Name: GTEX-111CU-2026-SM-5GZZC, Length: 56200, dtype: float64

In [25]:
filtered_muscle_expression_df = expression_df[all_muscle_samples]

processed_df, processed_info = preprocessor.preprocess_expression_data(
    filtered_muscle_expression_df,
    protein_coding,
    apply_log = True,
    filter_low_expr = True,
    filter_low_var = True,
    detect_outliers = True,
    min_expression=0.1,
    min_variance=0.1,
    outlier_contamination=0.05
)

Starting expression data preprocessing pipeline...
Filtered to 19124 protein coding genes (from 56200)
Applying log2(TPM + 1) transformation...
Filtered to 13638 genes (removed 5486 genes with low expression in > 20.0% of samples)
Filtered to 19124 protein coding genes (from 56200)
Applying log2(TPM + 1) transformation...
Filtered to 13638 genes (removed 5486 genes with low expression in > 20.0% of samples)
Filtered to 12325 genes with variance >= 0.1
Detecting outliers using TruncatedSVD with 20 components...
Filtered to 12325 genes with variance >= 0.1
Detecting outliers using TruncatedSVD with 20 components...
Detected 4 outlier samples
SVD explained variance ratio: [0.92396903 0.0163448  0.00956844 0.0042763  0.00315717]
Removed 4 outlier samples
Remaining samples: 798
Applying quantile normalization...
Detected 4 outlier samples
SVD explained variance ratio: [0.92396903 0.0163448  0.00956844 0.0042763  0.00315717]
Removed 4 outlier samples
Remaining samples: 798
Applying quantile 

In [24]:
processed_df.head()

GTEX-111CU-2026-SM-5GZZC  GTEX-113JC-2726-SM-5EGIS  \
ENSG00000187634.11                  0.330743                  0.627497   
ENSG00000188976.10                  5.922930                  5.679323   
ENSG00000187961.13                  1.995472                  1.775191   
ENSG00000187583.10                  0.294629                  0.992736   
ENSG00000187642.9                   6.209774                  8.516954   

                    GTEX-117YW-2426-SM-5Q5AE  GTEX-117YX-2526-SM-5EQ4Q  \
ENSG00000187634.11                  0.538273                  0.168728   
ENSG00000188976.10                  5.755679                  6.224135   
ENSG00000187961.13                  1.347724                  1.941918   
ENSG00000187583.10                  1.534590                  0.799456   
ENSG00000187642.9                   8.426669                  7.130217   

                    GTEX-1192X-0426-SM-5GIEE  GTEX-11DXW-0726-SM-5H12J  \
ENSG00000187634.11                  0.267884                  0.791886   
ENSG00000188976.10                  6.032826                  5.611052   
ENSG00000187961.13                  1.731807                  1.506002   
ENSG00000187583.10                  0.491380                  0.484509   
ENSG00000187642.9                   6.079198                  7.121830   

                    GTEX-11DXZ-2426-SM-5N9DT  GTEX-11DZ1-0926-SM-5EQ5R  \
ENSG00000187634.11                  0.625735                  0.453782   
ENSG00000188976.10                  5.771384                  6.161743   
ENSG00000187961.13                  1.633968                  1.918709   
ENSG00000187583.10                  0.725150                  0.215263   
ENSG00000187642.9                   7.443118                  3.591562   

                    GTEX-11EM3-2126-SM-5H11M  GTEX-11EQ9-2126-SM-5PNVW  ...  \
ENSG00000187634.11                  0.586393                  0.197103  ...   
ENSG00000188976.10                  6.013712                  6.333352  ...   
ENSG00000187961.13                  1.883142                  1.897592  ...   
ENSG00000187583.10                  0.652858                  0.144389  ...   
ENSG00000187642.9                   7.782680                  7.547938  ...   

                    GTEX-ZF28-0526-SM-4WKGW  GTEX-ZF29-2426-SM-DO92G  \
ENSG00000187634.11                 0.481680                 0.181560   
ENSG00000188976.10                 6.170170                 5.771384   
ENSG00000187961.13                 1.678300                 1.494642   
ENSG00000187583.10                 0.203059                 0.513514   
ENSG00000187642.9                  4.368726                 7.226472   

                    GTEX-ZLV1-2126-SM-4WWD2  GTEX-ZPCL-2026-SM-57WFD  \
ENSG00000187634.11                 0.297362                 1.113280   
ENSG00000188976.10                 6.531977                 5.754625   
ENSG00000187961.13                 2.057592                 2.113478   
ENSG00000187583.10                 0.415634                 0.399810   
ENSG00000187642.9                  6.985076                 6.633469   

                    GTEX-ZQG8-1226-SM-51MRX  GTEX-ZVT3-0526-SM-5GIE9  \
ENSG00000187634.11                 0.642248                 0.273588   
ENSG00000188976.10                 6.275220                 5.666519   
ENSG00000187961.13                 2.082115                 2.026758   
ENSG00000187583.10                 0.471369                 0.646954   
ENSG00000187642.9                  7.073370                 7.205314   

                    GTEX-ZXG5-0326-SM-5GICH  GTEX-ZYFG-2426-SM-5GIE8  \
ENSG00000187634.11                 0.608981                 0.373668   
ENSG00000188976.10                 6.209774                 6.360078   
ENSG00000187961.13                 1.363784                 2.035280   
ENSG00000187583.10                 0.396115                 0.379115   
ENSG00000187642.9                  5.637189                 5.926524   

                    GTEX-ZYW4-052

# Follow the instructions of the WORKFLOW_GUIDE.md

In [36]:
import streamlit as st
import pickle
import pandas as pd
import polars as pl
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from pathlib import Path
from typing import List, Dict, Tuple
from rich import print as rprint
import warnings
warnings.filterwarnings('ignore')

# Import custom modules
from new_script.data_reader import GTExDataReader
from new_script.preprocessing import DataPreprocessor
from new_script.network_analysis import NetworkAnalysis
from new_script.mdc_analysis import MDCAnalyzer
from new_script.visualization import NetworkVisualizer

In [21]:
reader = GTExDataReader()

target_tissues = ['Brain - Cortex', 'Muscle - Skeletal', 'Adipose - Subcutaneous']

Found data directory: /Users/edeneldar/CoExpression_ReProduction/data


In [22]:
reader.data_dir


PosixPath('data')

In [23]:
expression_df, gene_metadata = reader.read_gct_file(
    "GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_tpm.gct"
)

rprint("Expression DataFrame loaded successfully.")
display(expression_df.head())

rprint("Gene metadata loaded successfully.")
display(gene_metadata.head())


Reading GCT file: data/GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_tpm.gct
GCT version: #1.2
Dimensions: 56200 genes, 17382 samples
Preparing to read 17382 samples
Processed 1000/56200 genes (1.8%)...
Processed 2000/56200 genes (3.6%)...
Processed 3000/56200 genes (5.3%)...
Processed 4000/56200 genes (7.1%)...
Processed 5000/56200 genes (8.9%)...
Processed 6000/56200 genes (10.7%)...
Processed 7000/56200 genes (12.5%)...
Processed 8000/56200 genes (14.2%)...
Processed 9000/56200 genes (16.0%)...
Processed 10000/56200 genes (17.8%)...
Processed 11000/56200 genes (19.6%)...
Processed 12000/56200 genes (21.4%)...
Processed 13000/56200 genes (23.1%)...
Processed 14000/56200 genes (24.9%)...
Processed 15000/56200 genes (26.7%)...
Processed 16000/56200 genes (28.5%)...
Processed 17000/56200 genes (30.2%)...
Processed 18000/56200 genes (32.0%)...
Processed 19000/56200 genes (33.8%)...
Processed 20000/56200 genes (35.6%)...
Processed 21000/56200 genes (37.4%)...
Processed 22000/56200 genes 

Expression DataFrame loaded successfully.

GTEX-1117F-0226-SM-5GZZ7  GTEX-1117F-0426-SM-5EGHI  \
ENSG00000223972.5                   0.00000                     0.000   
ENSG00000227232.5                   8.76400                     3.861   
ENSG00000278267.1                   0.00000                     0.000   
ENSG00000243485.5                   0.07187                     0.000   
ENSG00000237613.2                   0.00000                     0.000   

                   GTEX-1117F-0526-SM-5EGHJ  GTEX-1117F-0626-SM-5N9CS  \
ENSG00000223972.5                     0.000                   0.00000   
ENSG00000227232.5                     7.349                  11.07000   
ENSG00000278267.1                     1.004                   0.00000   
ENSG00000243485.5                     0.000                   0.06761   
ENSG00000237613.2                     0.000                   0.00000   

                   GTEX-1117F-0726-SM-5GIEN  GTEX-1117F-1326-SM-5EGHH  \
ENSG00000223972.5                     0.000                     0.000   
ENSG00000227232.5                     3.306                     5.389   
ENSG00000278267.1                     0.000                     0.000   
ENSG00000243485.5                     0.000                     0.000   
ENSG00000237613.2                     0.000                     0.000   

                   GTEX-1117F-2426-SM-5EGGH  GTEX-1117F-2526-SM-5GZY6  \
ENSG00000223972.5                      0.00                   0.00000   
ENSG00000227232.5                     11.99                  16.95000   
ENSG00000278267.1                      0.00                   0.00000   
ENSG00000243485.5                      0.00                   0.00000   
ENSG00000237613.2                      0.00                   0.03904   

                   GTEX-1117F-2826-SM-5GZXL  GTEX-1117F-2926-SM-5GZYI  ...  \
ENSG00000223972.5                      0.00                   0.00000  ...   
ENSG00000227232.5                     10.04                  12.50000  ...   
ENSG00000278267.1                      0.00                   0.00000  ...   
ENSG00000243485.5                      0.00                   0.06265  ...   
ENSG00000237613.2                      0.00                   0.00000  ...   

                   GTEX-ZZPU-1126-SM-5N9CW  GTEX-ZZPU-1226-SM-5N9CK  \
ENSG00000223972.5                  0.00000                  0.03629   
ENSG00000227232.5                  1.60600                  2.26800   
ENSG00000278267.1                  0.00000                  0.00000   
ENSG00000243485.5                  0.00000                  0.00000   
ENSG00000237613.2                  0.02429                  0.00000   

                   GTEX-ZZPU-1326-SM-5GZWS  GTEX-ZZPU-1426-SM-5GZZ6  \
ENSG00000223972.5                  0.00000                     0.00   
ENSG00000227232.5                  5.38600                     2.31   
ENSG00000278267.1                  0.00000                     0.00   
ENSG00000243485.5                  0.06073                     0.00   
ENSG00000237613.2                  0.00000                     0.00   

                   GTEX-ZZPU-1826-SM-5E43L  GTEX-ZZPU-2126-SM-5EGIU  \
ENSG00000223972.5                  0.00000                   0.0000   
ENSG00000227232.5                  2.45600                   4.0230   
ENSG00000278267.1                  0.00000                   0.0000   
ENSG00000243485.5                  0.08464                   0.1435   
ENSG00000237613.2                  0.00000                   0.0000   

                   GTEX-ZZPU-2226-SM-5EGIV  GTEX-ZZPU-2426-SM-5E44I  \
ENSG00000223972.5                    0.000                  0.00000   
ENSG00000227232.5                    1.922                  2.85700   
ENSG00000278267.1                    0.000                  0.00000   
ENSG00000243485.5                    0.000                  0.05216   
ENSG00000237613.2                    0.000                  0.00000   

                   GTEX-ZZPU-2626-SM-5E45Y  GTEX-ZZPU-2726-SM-5NQ8O  
ENSG00000223972.

Gene metadata loaded successfully.

gene_id  description
ENSG00000223972.5  ENSG00000223972.5      DDX11L1
ENSG00000227232.5  ENSG00000227232.5       WASH7P
ENSG00000278267.1  ENSG00000278267.1    MIR6859-1
ENSG00000243485.5  ENSG00000243485.5  MIR1302-2HG
ENSG00000237613.2  ENSG00000237613.2      FAM138A

In [46]:
import tarfile

eqtl_cov_file = tarfile.open(r"data/GTEx_Analysis_v8_eQTL_covariates.tar.gz", "r:gz")
eqtl_file = tarfile.open(r"/Users/edeneldar/CoExpression_reProduction/data/GTEx_Analysis_v8_eQTL_expression_matrices.tar", "r:*")

In [31]:
eqtl_file.extractall(r"/Users/edeneldar/CoExpression_reProduction/data/eqtl_matrices")

In [48]:
eqtl_cov_file.extractall(r"/Users/edeneldar/CoExpression_reProduction/data/eqtl_matrices")

In [49]:
import os

os.listdir(r"/Users/edeneldar/CoExpression_reProduction/data/eqtl_matrices/GTEx_Analysis_v8_eQTL_covariates")

['Brain_Hypothalamus.v8.covariates.txt',
 'Adipose_Subcutaneous.v8.covariates.txt',
 'Brain_Nucleus_accumbens_basal_ganglia.v8.covariates.txt',
 'Lung.v8.covariates.txt',
 'Artery_Tibial.v8.covariates.txt',
 'Small_Intestine_Terminal_Ileum.v8.covariates.txt',
 'Skin_Sun_Exposed_Lower_leg.v8.covariates.txt',
 'Whole_Blood.v8.covariates.txt',
 'Cells_Cultured_fibroblasts.v8.covariates.txt',
 'Thyroid.v8.covariates.txt',
 'Brain_Putamen_basal_ganglia.v8.covariates.txt',
 'Brain_Anterior_cingulate_cortex_BA24.v8.covariates.txt',
 'Esophagus_Mucosa.v8.covariates.txt',
 'Adrenal_Gland.v8.covariates.txt',
 'Spleen.v8.covariates.txt',
 'Prostate.v8.covariates.txt',
 'Stomach.v8.covariates.txt',
 'Heart_Left_Ventricle.v8.covariates.txt',
 'Minor_Salivary_Gland.v8.covariates.txt',
 'Uterus.v8.covariates.txt',
 'Nerve_Tibial.v8.covariates.txt',
 'Colon_Sigmoid.v8.covariates.txt',
 'Muscle_Skeletal.v8.covariates.txt',
 'Pancreas.v8.covariates.txt',
 'Ovary.v8.covariates.txt',
 'Brain_Caudate_basal

In [ ]:
pl.read_csv(
    r"data/eqtl_matrices/GTEx_Analysis_v8_eQTL_expression_matrices/Adipose_Subcutaneous.v8.normalized_expression.bed.gz",
    # comment_prefix='#',
    separator='\t',
    # has_header=False
).select("gene_id").null_count()

polars.dataframe.frame.DataFrame

In [44]:
pl_df = pl.read_csv(
    r"data/eqtl_matrices/GTEx_Analysis_v8_eQTL_expression_matrices/Adipose_Subcutaneous.v8.normalized_expression.bed.gz",
    # comment_prefix='#',
    separator='\t',
    # has_header=False
).head()

In [45]:
pl_df

shape: (5, 585)
┌──────┬────────┬────────┬───────────────────┬───┬───────────┬───────────┬───────────┬───────────┐
│ #chr ┆ start  ┆ end    ┆ gene_id           ┆ … ┆ GTEX-ZYW4 ┆ GTEX-ZYY3 ┆ GTEX-ZZ64 ┆ GTEX-ZZPU │
│ ---  ┆ ---    ┆ ---    ┆ ---               ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---       │
│ str  ┆ i64    ┆ i64    ┆ str               ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64       │
╞══════╪════════╪════════╪═══════════════════╪═══╪═══════════╪═══════════╪═══════════╪═══════════╡
│ chr1 ┆ 29552  ┆ 29553  ┆ ENSG00000227232.5 ┆ … ┆ -2.25625  ┆ 0.279229  ┆ 0.421295  ┆ -1.423335 │
│ chr1 ┆ 135894 ┆ 135895 ┆ ENSG00000268903.1 ┆ … ┆ 0.234711  ┆ 1.423335  ┆ -0.856443 ┆ 1.002398  │
│ chr1 ┆ 137964 ┆ 137965 ┆ ENSG00000269981.1 ┆ … ┆ 0.28371   ┆ 1.630041  ┆ -1.084032 ┆ 1.226711  │
│ chr1 ┆ 173861 ┆ 173862 ┆ ENSG00000241860.6 ┆ … ┆ 0.449708  ┆ 0.239141  ┆ -1.313533 ┆ 0.819728  │
│ chr1 ┆ 195410 ┆ 195411 ┆ ENSG00000279457.4 ┆ … ┆ 0.655684  ┆ 0.623972  ┆ 0.57246   ┆ -0.894351 │
└──────┴────────┴────────┴───────────────────┴───┴───────────┴───────────┴───────────┴───────────┘

In [35]:
pd.read_table(
    r"data/eqtl_matrices/GTEx_Analysis_v8_eQTL_expression_matrices/Adipose_Subcutaneous.v8.normalized_expression.bed.gz",
    comment='#',
    low_memory=False,
    header=None
).head()

0       1       2                  3         4         5         6    \
0  chr1   29552   29553  ENSG00000227232.5  1.313533 -0.900794 -0.292690   
1  chr1  135894  135895  ENSG00000268903.1 -0.397876  0.572460 -1.091816   
2  chr1  137964  137965  ENSG00000269981.1  0.060333  0.995306 -0.844079   
3  chr1  173861  173862  ENSG00000241860.6  0.225866 -0.819728 -0.234711   
4  chr1  195410  195411  ENSG00000279457.4  0.292690 -1.002398  0.402542   

        7         8         9    ...       575       576       577       578  \
0 -0.732411 -0.274754 -0.699026  ... -0.347092  0.527368  1.976396  1.776799   
1  2.115771  0.103551  0.129569  ... -0.666401 -0.850245 -1.447466  1.038647   
2  2.314897  0.618748  0.704535  ...  0.077602 -1.046061 -1.776799 -1.115573   
3  1.068659  0.261361  1.123634  ...  2.204469 -1.366375 -1.553621 -1.698852   
4 -0.542275 -1.776799 -0.552281  ...  0.297188  1.447466 -1.156632  2.256250   

        579       580       581       582       583       584  
0 -0.324309 -0.894351 -2.256250  0.279229  0.421295 -1.423335  
1 -1.303395 -0.347092  0.234711  1.423335 -0.856443  1.002398  
2 -0.807734  0.488170  0.283710  1.630041 -1.084032  1.226711  
3 -0.532324 -0.310720  0.449708  0.239141 -1.313533  0.819728  
4  0.582637 -0.195041  0.655684  0.623972  0.572460 -0.894351  

[5 rows x 585 columns]

In [25]:
sample_attrs = reader.read_sample_attributes()
subject_phenos = reader.read_subject_phenotypes()

rprint("Sample attributes loaded successfully.")
display(sample_attrs.head())

rprint("Subject phenotypes loaded successfully.")
display(subject_phenos.head())


Reading sample attributes: data/GTEx_Analysis_v8_Annotations_SampleAttributesDS.tsv
Loaded sample attributes: (22951, 62)
Reading subject phenotypes: data/GTEx_Analysis_v8_Annotations_SubjectPhenotypesDS.tsv
Loaded subject phenotypes: (980, 3)


Sample attributes loaded successfully.

SMATSSCR SMCENTER SMPTHNTS  SMRIN   SMTS  \
SAMPID                                                                    
GTEX-1117F-0003-SM-58Q7G            NaN       B1      NaN    NaN  Blood   
GTEX-1117F-0003-SM-5DWSB            NaN       B1      NaN    NaN  Blood   
GTEX-1117F-0003-SM-6WBT7            NaN       B1      NaN    NaN  Blood   
GTEX-1117F-0011-R10a-SM-AHZ7F       NaN   B1, A1      NaN    NaN  Brain   
GTEX-1117F-0011-R10b-SM-CYKQ8       NaN   B1, A1      NaN    7.2  Brain   

                                                      SMTSD  SMUBRID  \
SAMPID                                                                 
GTEX-1117F-0003-SM-58Q7G                        Whole Blood  0013756   
GTEX-1117F-0003-SM-5DWSB                        Whole Blood  0013756   
GTEX-1117F-0003-SM-6WBT7                        Whole Blood  0013756   
GTEX-1117F-0011-R10a-SM-AHZ7F  Brain - Frontal Cortex (BA9)  0009834   
GTEX-1117F-0011-R10b-SM-CYKQ8  Brain - Frontal Cortex (BA9)  0009834   

                               SMTSISCH  SMTSPAX  SMNABTCH  ... SME1ANTI  \
SAMPID                                                      ...            
GTEX-1117F-0003-SM-58Q7G         1188.0      NaN  BP-38516  ...      NaN   
GTEX-1117F-0003-SM-5DWSB         1188.0      NaN  BP-38516  ...      NaN   
GTEX-1117F-0003-SM-6WBT7         1188.0      NaN  BP-38516  ...      NaN   
GTEX-1117F-0011-R10a-SM-AHZ7F    1193.0      NaN       NaN  ...      NaN   
GTEX-1117F-0011-R10b-SM-CYKQ8    1193.0      NaN  BP-42319  ...      NaN   

                              SMSPLTRD SMBSMMRT SME1SNSE SME1PCTS SMRRNART  \
SAMPID                                                                       
GTEX-1117F-0003-SM-58Q7G           NaN      NaN      NaN      NaN      NaN   
GTEX-1117F-0003-SM-5DWSB           NaN      NaN      NaN      NaN      NaN   
GTEX-1117F-0003-SM-6WBT7           NaN      NaN      NaN      NaN      NaN   
GTEX-1117F-0011-R10a-SM-AHZ7F      NaN      NaN      NaN      NaN      NaN   
GTEX-1117F-0011-R10b-SM-CYKQ8      NaN      NaN      NaN      NaN      NaN   

                              SME1MPRT  SMNUM5CD  SMDPMPRT  SME2PCTS  
SAMPID                                                                
GTEX-1117F-0003-SM-58Q7G           NaN       NaN       NaN       NaN  
GTEX-1117F-0003-SM-5DWSB           NaN       NaN       NaN       NaN  
GTEX-1117F-0003-SM-6WBT7           NaN       NaN       NaN       NaN  
GTEX-1117F-0011-R10a-SM-AHZ7F      NaN       NaN       NaN       NaN  
GTEX-1117F-0011-R10b-SM-CYKQ8      NaN       NaN       NaN       NaN  

[5 rows x 62 columns]

Subject phenotypes loaded successfully.

SEX    AGE  DTHHRDY
SUBJID                         
GTEX-1117F    2  60-69      4.0
GTEX-111CU    1  50-59      0.0
GTEX-111FC    1  60-69      1.0
GTEX-111VG    1  60-69      3.0
GTEX-111YS    1  60-69      0.0

In [26]:
with open("expression_df.pkl", "wb") as f:
    pickle.dump(expression_df, f)

with open("gene_metadata.pkl", "wb") as f:
    pickle.dump(gene_metadata, f)

KeyboardInterrupt: 

In [54]:
expression_df, sample_attrs, subject_phenos = reader.align_expression_with_metadata(
    expression_df, sample_attrs, subject_phenos
)

rprint("Expression data and metadata successfully aligned.")

Aligning expression data with metadata...
Expression data samples: 17382
Sample attributes: 22951
Subject phenotypes: 980
Common samples (expression + attributes): 17382
Extracting subject IDs...
Common subjects (expression + phenotypes): 948
Final samples after subject filtering: 17382
Filtering datasets...
Final aligned datasets:
  Expression: (56200, 17382)
  Sample attributes: (17382, 62)
  Subject phenotypes: (948, 3)


Expression data and metadata successfully aligned.

In [55]:
tissue_young_samples = {}
tissue_old_samples = {}

for tissue in target_tissues:
    tissue_young_samples[tissue] = reader.filter_samples_by_metadata(
        sample_attrs, 
        subject_phenos, 
        tissue=tissue, 
        age_group='young'
    )

    tissue_old_samples[tissue] = reader.filter_samples_by_metadata(
        sample_attrs, 
        subject_phenos, 
        tissue=tissue, 
        age_group='old'
    )

After RIN >= 5.7: 17046 samples
After tissue filter (Brain - Cortex): 246 samples
   Extracted 246 subject IDs from 246 samples
   Samples with valid subject IDs: 246
   Samples with phenotype data: 246
After age group filter (young): 115 samples
After RIN >= 5.7: 17046 samples
After tissue filter (Brain - Cortex): 246 samples
   Extracted 246 subject IDs from 246 samples
   Samples with valid subject IDs: 246
   Samples with phenotype data: 246
After age group filter (old): 131 samples
After RIN >= 5.7: 17046 samples
After tissue filter (Muscle - Skeletal): 802 samples
   Extracted 802 subject IDs from 802 samples
   Samples with valid subject IDs: 802
   Samples with phenotype data: 802
After age group filter (young): 510 samples
After RIN >= 5.7: 17046 samples
After tissue filter (Muscle - Skeletal): 802 samples
   Extracted 802 subject IDs from 802 samples
   Samples with valid subject IDs: 802
   Samples with phenotype data: 802
After age group filter (old): 292 samples
After RIN 

In [7]:
# Add this cell to check what files exist
import os
data_dir = reader.data_dir
print(f"Data directory: {data_dir}")
print(f"Files in data directory:")
for file in os.listdir(data_dir):
    print(f"  {file}")

Data directory: ../data
Files in data directory:
  einat_steps_2024-01-10.json
  einat_steps_2024-01-06.json
  einat_steps_2023-12-31.json
  einat_steps_2023-12-27.json
  einat_steps_2023-12-26.json
  einat_steps_2023-12-30.json
  einat_steps_2024-01-07.json
  einat_steps_2023-12-17.json
  einat_steps_2023-12-21.json
  einat_steps_2023-12-20.json
  einat_steps_2024-01-01.json
  einat_steps_2023-12-16.json
  libs
  einat_steps_2023-12-15.json
  einat_steps_2023-12-23.json
  einat_steps_2024-01-02.json
  einat_steps_2023-12-19.json
  einat_steps_2023-12-18.json
  einat_steps_2024-01-03.json
  einat_steps_2023-12-22.json
  einat_steps_2023-12-14.json
  einat_steps_2023-12-25.json
  einat_steps_2024-01-04.json
  einat_steps_2023-12-29.json
  einat_steps_2024-01-08.json
  einat_steps_2024-01-09.json
  einat_steps_2023-12-28.json
  einat_steps_2024-01-05.json
  einat_steps_2023-12-24.json


In [58]:
hgnc_data = reader.read_protein_coding_genes(r'hgnc_complete_set.tsv')

Reading HGNC data: data/hgnc_complete_set.tsv
Found 19293 protein coding genes


In [61]:
hgnc_data

hgnc_id   symbol                                  name  \
0          HGNC:5     A1BG                alpha-1-B glycoprotein   
2      HGNC:24086     A1CF        APOBEC1 complementation factor   
3          HGNC:7      A2M                 alpha-2-macroglobulin   
5      HGNC:23336    A2ML1          alpha-2-macroglobulin like 1   
9      HGNC:30005  A3GALT2     alpha 1,3-galactosyltransferase 2   
...           ...      ...                                   ...   
44237   HGNC:3547     F8A1  coagulation factor VIII associated 1   
44238  HGNC:31849     F8A2  coagulation factor VIII associated 2   
44239  HGNC:31850     F8A3  coagulation factor VIII associated 3   
44240   HGNC:3551       F9                 coagulation factor IX   
44241   HGNC:3528      F10                  coagulation factor X   

               locus_group                 locus_type    status  location  \
0      protein-coding gene  gene with protein product  Approved  19q13.43   
2      protein-coding gene  gene with protein product  Approved  10q11.23   
3      protein-coding gene  gene with protein product  Approved  12p13.31   
5      protein-coding gene  gene with protein product  Approved  12p13.31   
9      protein-coding gene  gene with protein product  Approved    1p35.1   
...                    ...                        ...       ...       ...   
44237  protein-coding gene  gene with protein product  Approved      Xq28   
44238  protein-coding gene  gene with protein product  Approved      Xq28   
44239  protein-coding gene  gene with protein product  Approved      Xq28   
44240  protein-coding gene  gene with protein product  Approved    Xq27.1   
44241  protein-coding gene  gene with protein product  Approved     13q34   

      location_sortable                   alias_symbol  \
0              19q13.43                            NaN   
2              10q11.23  ACF|ASP|ACF64|ACF65|APOBEC1CF   
3              12p13.31           FWP007|S863-7|CPAMD5   
5              12p13.31                  FLJ25179|p170   
9               01p35.1                   IGBS3S|IGB3S   
...                 ...                            ...   
44237              Xq28                        DXS522E   
44238              Xq28                            NaN   
44239              Xq28                            NaN   
44240            Xq27.1                            FIX   
44241             13q34                            NaN   

                                              alias_name  ...   cd lncrnadb  \
0                                                    NaN  ...  NaN      NaN   
2                                                    NaN  ...  NaN      NaN   
3                                                    NaN  ...  NaN      NaN   
5                                                    NaN  ...  NaN      NaN   
9        iGb3 synthase|isoglobotriaosylceramide synthase  ...  NaN      NaN   
...                                                  ...  ...  ...      ...   
44237                                                NaN  ...  NaN      NaN   
44238                                                NaN  ...  NaN      NaN   
44239                                                NaN  ...  NaN      NaN   
44240  Factor IX|plasma thromboplastic component|Chri...  ...  NaN      NaN   
44241                                                NaN  ...  NaN      NaN   

       enzyme_id intermediate_filament_db rna_central_id lncipedia gtrnadb  \
0            NaN                      NaN            NaN       NaN     NaN   
2            NaN                      NaN            NaN       NaN     NaN   
3            NaN                      NaN            NaN       NaN     NaN   
5            NaN                      NaN            NaN       NaN     NaN   
9            NaN                      NaN            NaN       NaN     NaN   
...          ...                      ...            ...       ...     ...   
44237        NaN                      NaN            NaN       NaN     NaN  

In [59]:
expression_df.head()

GTEX-1117F-0226-SM-5GZZ7  GTEX-1117F-0426-SM-5EGHI  \
ENSG00000223972.5                   0.00000                     0.000   
ENSG00000227232.5                   8.76400                     3.861   
ENSG00000278267.1                   0.00000                     0.000   
ENSG00000243485.5                   0.07187                     0.000   
ENSG00000237613.2                   0.00000                     0.000   

                   GTEX-1117F-0526-SM-5EGHJ  GTEX-1117F-0626-SM-5N9CS  \
ENSG00000223972.5                     0.000                   0.00000   
ENSG00000227232.5                     7.349                  11.07000   
ENSG00000278267.1                     1.004                   0.00000   
ENSG00000243485.5                     0.000                   0.06761   
ENSG00000237613.2                     0.000                   0.00000   

                   GTEX-1117F-0726-SM-5GIEN  GTEX-1117F-1326-SM-5EGHH  \
ENSG00000223972.5                     0.000                     0.000   
ENSG00000227232.5                     3.306                     5.389   
ENSG00000278267.1                     0.000                     0.000   
ENSG00000243485.5                     0.000                     0.000   
ENSG00000237613.2                     0.000                     0.000   

                   GTEX-1117F-2426-SM-5EGGH  GTEX-1117F-2526-SM-5GZY6  \
ENSG00000223972.5                      0.00                   0.00000   
ENSG00000227232.5                     11.99                  16.95000   
ENSG00000278267.1                      0.00                   0.00000   
ENSG00000243485.5                      0.00                   0.00000   
ENSG00000237613.2                      0.00                   0.03904   

                   GTEX-1117F-2826-SM-5GZXL  GTEX-1117F-2926-SM-5GZYI  ...  \
ENSG00000223972.5                      0.00                   0.00000  ...   
ENSG00000227232.5                     10.04                  12.50000  ...   
ENSG00000278267.1                      0.00                   0.00000  ...   
ENSG00000243485.5                      0.00                   0.06265  ...   
ENSG00000237613.2                      0.00                   0.00000  ...   

                   GTEX-ZZPU-1126-SM-5N9CW  GTEX-ZZPU-1226-SM-5N9CK  \
ENSG00000223972.5                  0.00000                  0.03629   
ENSG00000227232.5                  1.60600                  2.26800   
ENSG00000278267.1                  0.00000                  0.00000   
ENSG00000243485.5                  0.00000                  0.00000   
ENSG00000237613.2                  0.02429                  0.00000   

                   GTEX-ZZPU-1326-SM-5GZWS  GTEX-ZZPU-1426-SM-5GZZ6  \
ENSG00000223972.5                  0.00000                     0.00   
ENSG00000227232.5                  5.38600                     2.31   
ENSG00000278267.1                  0.00000                     0.00   
ENSG00000243485.5                  0.06073                     0.00   
ENSG00000237613.2                  0.00000                     0.00   

                   GTEX-ZZPU-1826-SM-5E43L  GTEX-ZZPU-2126-SM-5EGIU  \
ENSG00000223972.5                  0.00000                   0.0000   
ENSG00000227232.5                  2.45600                   4.0230   
ENSG00000278267.1                  0.00000                   0.0000   
ENSG00000243485.5                  0.08464                   0.1435   
ENSG00000237613.2                  0.00000                   0.0000   

                   GTEX-ZZPU-2226-SM-5EGIV  GTEX-ZZPU-2426-SM-5E44I  \
ENSG00000223972.5                    0.000                  0.00000   
ENSG00000227232.5                    1.922                  2.85700   
ENSG00000278267.1                    0.000                  0.00000   
ENSG00000243485.5                    0.000                  0.05216   
ENSG00000237613.2                    0.000                  0.00000   

                   GTEX-ZZPU-2626-SM-5E45Y  GTEX-ZZPU-2726-SM-5NQ8O  
ENSG00000223972.

In [60]:
preprocessor = DataPreprocessor()

tissue_processed_data = {}

for tissue in target_tissues:
    rprint(f"Processing tissue: {tissue}")
    
    tissue_samples = tissue_young_samples[tissue] + tissue_old_samples[tissue]
    tissue_expression_df = expression_df[tissue_samples]

    processed_tissue, info = preprocessor.preprocess_expression_data(
        expression_df=tissue_expression_df,
        hgnc_data=hgnc_data,
        sample_attrs=sample_attrs,
        subject_phenos=subject_phenos,
        apply_log=True,
        filter_low_expr=True,
        filter_low_var=True,
        detect_outliers=True,
        quantile_norm= True,
        regress_confounders= True,
        min_expression=0.1,
        min_variance=0,
        outlier_contamination=0.02
    )

    processed_tissue.index = [f"{tissue}_{gene}" for gene in processed_tissue.index]
    tissue_processed_data[tissue] = processed_tissue

Processing tissue: Brain - Cortex

Starting expression data preprocessing pipeline...
Filtered to 19124 protein coding genes (from 56200)
Applying log2(TPM + 1) transformation...
Filtered to 15509 genes (removed 3615 genes with low expression in > 20.0% of samples)
Filtered to 15509 genes with variance >= 0
Detecting outliers using TruncatedSVD with 20 components...
Detected 7 outlier samples
SVD explained variance ratio: [0.9560008  0.01255942 0.00455406 0.00400028 0.00208922]
Removed 7 outlier samples
Remaining samples: 239
Applying quantile normalization...
Quantile normalization completed
No confounders provided - generating from GTEx metadata following original script methodology
Regressing out confounding factors using vectorized approach...
Starting vectorized confounding regression...
Generating confounders DataFrame from GTEx metadata following original script...
Processed 63 valid batches, 65 rare batches grouped as singletons
Converted AGE from ranges to numeric values (first 2 characters)
DEBUG: Final confou

Processing tissue: Muscle - Skeletal

Starting expression data preprocessing pipeline...
Filtered to 19124 protein coding genes (from 56200)
Applying log2(TPM + 1) transformation...
Filtered to 13638 genes (removed 5486 genes with low expression in > 20.0% of samples)
Filtered to 13638 genes with variance >= 0
Detecting outliers using TruncatedSVD with 20 components...
Detected 3 outlier samples
SVD explained variance ratio: [0.93541674 0.01374685 0.00812124 0.00361363 0.00267942]
Removed 3 outlier samples
Remaining samples: 799
Applying quantile normalization...
Quantile normalization completed
No confounders provided - generating from GTEx metadata following original script methodology
Regressing out confounding factors using vectorized approach...
Starting vectorized confounding regression...
Generating confounders DataFrame from GTEx metadata following original script...
Processed 154 valid batches, 54 rare batches grouped as singletons
Converted AGE from ranges to numeric values (first 2 characters)
DEBUG: Final confo

Processing tissue: Adipose - Subcutaneous

Starting expression data preprocessing pipeline...
Filtered to 19124 protein coding genes (from 56200)
Applying log2(TPM + 1) transformation...
Filtered to 14960 genes (removed 4164 genes with low expression in > 20.0% of samples)
Filtered to 14960 genes with variance >= 0
Detecting outliers using TruncatedSVD with 20 components...
Detected 5 outlier samples
SVD explained variance ratio: [0.94061601 0.01088636 0.00496208 0.00412969 0.0032028 ]
Removed 5 outlier samples
Remaining samples: 643
Applying quantile normalization...
Quantile normalization completed
No confounders provided - generating from GTEx metadata following original script methodology
Regressing out confounding factors using vectorized approach...
Starting vectorized confounding regression...
Generating confounders DataFrame from GTEx metadata following original script...
Processed 137 valid batches, 54 rare batches grouped as singletons
Converted AGE from ranges to numeric values (first 2 characters)
DEBUG: Final confo

In [62]:
# Identify common genes across all tissues (before prefixing)
common_genes = set(expression_df.index)

for tissue_data in tissue_processed_data.values():
    tissue_genes = set([gene.split('_',1)[1] for gene in tissue_data.index])
    common_genes = common_genes.intersection(tissue_genes)

rprint(f"Common genes across all tissues: {len(common_genes)}")


Common genes across all tissues: 13194

In [65]:
tissue_processed_data['Muscle - Skeletal'].head()

GTEX-111CU-2026-SM-5GZZC  \
Muscle - Skeletal_ENSG00000187634.11                 -0.139822   
Muscle - Skeletal_ENSG00000188976.10                  0.032776   
Muscle - Skeletal_ENSG00000187961.13                 -0.036930   
Muscle - Skeletal_ENSG00000187583.10                 -0.447160   
Muscle - Skeletal_ENSG00000187642.9                  -0.953558   

                                      GTEX-113JC-2726-SM-5EGIS  \
Muscle - Skeletal_ENSG00000187634.11                  0.184656   
Muscle - Skeletal_ENSG00000188976.10                 -0.210579   
Muscle - Skeletal_ENSG00000187961.13                  0.279011   
Muscle - Skeletal_ENSG00000187583.10                  0.263574   
Muscle - Skeletal_ENSG00000187642.9                   2.034278   

                                      GTEX-117YW-2426-SM-5Q5AE  \
Muscle - Skeletal_ENSG00000187634.11                  0.055125   
Muscle - Skeletal_ENSG00000188976.10                  0.111691   
Muscle - Skeletal_ENSG00000187961.13                 -0.253331   
Muscle - Skeletal_ENSG00000187583.10                  0.411465   
Muscle - Skeletal_ENSG00000187642.9                  -0.168211   

                                      GTEX-117YX-2526-SM-5EQ4Q  \
Muscle - Skeletal_ENSG00000187634.11                 -0.301348   
Muscle - Skeletal_ENSG00000188976.10                  0.178568   
Muscle - Skeletal_ENSG00000187961.13                  0.073296   
Muscle - Skeletal_ENSG00000187583.10                  0.130728   
Muscle - Skeletal_ENSG00000187642.9                   1.091318   

                                      GTEX-1192X-0426-SM-5GIEE  \
Muscle - Skeletal_ENSG00000187634.11                 -0.059495   
Muscle - Skeletal_ENSG00000188976.10                  0.098973   
Muscle - Skeletal_ENSG00000187961.13                  0.075864   
Muscle - Skeletal_ENSG00000187583.10                 -0.218990   
Muscle - Skeletal_ENSG00000187642.9                  -0.698382   

                                      GTEX-11DXW-0726-SM-5H12J  \
Muscle - Skeletal_ENSG00000187634.11                  0.067802   
Muscle - Skeletal_ENSG00000188976.10                  0.005085   
Muscle - Skeletal_ENSG00000187961.13                 -0.212629   
Muscle - Skeletal_ENSG00000187583.10                 -0.211527   
Muscle - Skeletal_ENSG00000187642.9                  -0.612346   

                                      GTEX-11DXZ-2426-SM-5N9DT  \
Muscle - Skeletal_ENSG00000187634.11                  0.085522   
Muscle - Skeletal_ENSG00000188976.10                  0.043805   
Muscle - Skeletal_ENSG00000187961.13                  0.139343   
Muscle - Skeletal_ENSG00000187583.10                  0.167492   
Muscle - Skeletal_ENSG00000187642.9                   1.054105   

                                      GTEX-11DZ1-0926-SM-5EQ5R  \
Muscle - Skeletal_ENSG00000187634.11                  0.085154   
Muscle - Skeletal_ENSG00000188976.10                  0.368861   
Muscle - Skeletal_ENSG00000187961.13                 -0.217224   
Muscle - Skeletal_ENSG00000187583.10                 -0.617143   
Muscle - Skeletal_ENSG00000187642.9                  -2.675487   

                                      GTEX-11EM3-2126-SM-5H11M  \
Muscle - Skeletal_ENSG00000187634.11                  0.037033   
Muscle - Skeletal_ENSG00000188976.10                 -0.081140   
Muscle - Skeletal_ENSG00000187961.13                  0.053981   
Muscle - Skeletal_ENSG00000187583.10                  0.200834   
Muscle - Skeletal_ENSG00000187642.9                   0.769179   

                                      GTEX-11EQ9-2126-SM-5PNVW  ...  \
Muscle - Skeletal_ENSG00000187634.11                 -0.193287  ...   
Muscle - Skeletal_ENSG00000188976.10                  0.232562  ...   
Muscle - Skeletal_ENSG00000187961.13                  0.059690  ...   
Muscle - Skeletal_ENSG00000187583.10                 -0.420928  ...   
Muscle - Skeletal_ENSG00000187642.9                   0.700716  ...   

                                      

In [11]:
type(tissue_processed_data)

with open("tissue_processed_data.pkl", "wb") as f:
    import pickle
    pickle.dump(tissue_processed_data, f)

In [16]:
with open("tissue_processed_data.pkl", "rb") as f:
    tissue_processed_data = pickle.load(f)

In [74]:
all_processed_data = pd.concat(tissue_processed_data.values(), axis=0)
all_processed_data['tissue'] = all_processed_data.index.str.split('_').str[0]
all_processed_data['gene'] = all_processed_data.index.str.split('_').str[1]

expression_columns = all_processed_data.columns[:-2]
all_processed_data = pd.concat([all_processed_data["tissue"], all_processed_data["gene"], all_processed_data[expression_columns]], axis=1)


In [75]:
all_processed_data.head()

tissue                gene  \
Brain - Cortex_ENSG00000187634.11  Brain - Cortex  ENSG00000187634.11   
Brain - Cortex_ENSG00000188976.10  Brain - Cortex  ENSG00000188976.10   
Brain - Cortex_ENSG00000187961.13  Brain - Cortex  ENSG00000187961.13   
Brain - Cortex_ENSG00000187583.10  Brain - Cortex  ENSG00000187583.10   
Brain - Cortex_ENSG00000187642.9   Brain - Cortex   ENSG00000187642.9   

                                   GTEX-1192X-3126-SM-5N9BY  \
Brain - Cortex_ENSG00000187634.11                  0.223804   
Brain - Cortex_ENSG00000188976.10                 -0.210749   
Brain - Cortex_ENSG00000187961.13                  0.446518   
Brain - Cortex_ENSG00000187583.10                 -0.395457   
Brain - Cortex_ENSG00000187642.9                  -0.071322   

                                   GTEX-11DXW-1126-SM-5H12Q  \
Brain - Cortex_ENSG00000187634.11                 -0.277158   
Brain - Cortex_ENSG00000188976.10                  0.134703   
Brain - Cortex_ENSG00000187961.13                 -0.237530   
Brain - Cortex_ENSG00000187583.10                  0.134022   
Brain - Cortex_ENSG00000187642.9                   0.201915   

                                   GTEX-11NUK-2926-SM-5A5MD  \
Brain - Cortex_ENSG00000187634.11                 -0.066278   
Brain - Cortex_ENSG00000188976.10                  0.033137   
Brain - Cortex_ENSG00000187961.13                 -0.145010   
Brain - Cortex_ENSG00000187583.10                 -0.011115   
Brain - Cortex_ENSG00000187642.9                   0.043859   

                                   GTEX-11O72-2926-SM-5BC4V  \
Brain - Cortex_ENSG00000187634.11                  0.181506   
Brain - Cortex_ENSG00000188976.10                  0.036487   
Brain - Cortex_ENSG00000187961.13                  0.078290   
Brain - Cortex_ENSG00000187583.10                 -0.068303   
Brain - Cortex_ENSG00000187642.9                  -0.025537   

                                   GTEX-11PRG-2926-SM-5987A  \
Brain - Cortex_ENSG00000187634.11                 -0.155149   
Brain - Cortex_ENSG00000188976.10                  0.050835   
Brain - Cortex_ENSG00000187961.13                 -0.161936   
Brain - Cortex_ENSG00000187583.10                  0.203230   
Brain - Cortex_ENSG00000187642.9                   0.159873   

                                   GTEX-11WQK-3026-SM-5EQL6  \
Brain - Cortex_ENSG00000187634.11                  0.368992   
Brain - Cortex_ENSG00000188976.10                 -0.146515   
Brain - Cortex_ENSG00000187961.13                 -0.117322   
Brain - Cortex_ENSG00000187583.10                 -0.098294   
Brain - Cortex_ENSG00000187642.9                   0.197115   

                                   GTEX-11ZUS-2926-SM-5FQSL  \
Brain - Cortex_ENSG00000187634.11                  0.136117   
Brain - Cortex_ENSG00000188976.10                  0.122047   
Brain - Cortex_ENSG00000187961.13                  0.103604   
Brain - Cortex_ENSG00000187583.10                 -0.052249   
Brain - Cortex_ENSG00000187642.9                  -0.141553   

                                   GTEX-12126-1026-SM-5P9JJ  ...  \
Brain - Cortex_ENSG00000187634.11                  0.011542  ...   
Brain - Cortex_ENSG00000188976.10                  0.107677  ...   
Brain - Cortex_ENSG00000187961.13                 -0.153550  ...   
Brain - Cortex_ENSG00000187583.10                 -0.056412  ...   
Brain - Cortex_ENSG00000187642.9                   0.024519  ...   

                                   GTEX-ZDXO-2426-SM-5S2NJ  \
Brain - Cortex_ENSG00000187634.11                      NaN   
Brain - Cortex_ENSG00000188976.10                      NaN   
Brain - Cortex_ENSG00000187961.13                      NaN   
Brain - Cortex_ENSG00000187583.10                      NaN   
Brain - Cortex_ENSG00000187642.9                       NaN   

                                   GTEX-ZE9C-2826-SM-5S2MO  \
Brain - Cortex_ENSG00000187634.11                      NaN   
Brain - Cortex_ENSG00000188976.10            

In [76]:
all_processed_data_clean = all_processed_data.dropna(how='all', subset=expression_columns)

In [77]:
all_processed_data_clean.head()

tissue                gene  \
Brain - Cortex_ENSG00000187634.11  Brain - Cortex  ENSG00000187634.11   
Brain - Cortex_ENSG00000188976.10  Brain - Cortex  ENSG00000188976.10   
Brain - Cortex_ENSG00000187961.13  Brain - Cortex  ENSG00000187961.13   
Brain - Cortex_ENSG00000187583.10  Brain - Cortex  ENSG00000187583.10   
Brain - Cortex_ENSG00000187642.9   Brain - Cortex   ENSG00000187642.9   

                                   GTEX-1192X-3126-SM-5N9BY  \
Brain - Cortex_ENSG00000187634.11                  0.223804   
Brain - Cortex_ENSG00000188976.10                 -0.210749   
Brain - Cortex_ENSG00000187961.13                  0.446518   
Brain - Cortex_ENSG00000187583.10                 -0.395457   
Brain - Cortex_ENSG00000187642.9                  -0.071322   

                                   GTEX-11DXW-1126-SM-5H12Q  \
Brain - Cortex_ENSG00000187634.11                 -0.277158   
Brain - Cortex_ENSG00000188976.10                  0.134703   
Brain - Cortex_ENSG00000187961.13                 -0.237530   
Brain - Cortex_ENSG00000187583.10                  0.134022   
Brain - Cortex_ENSG00000187642.9                   0.201915   

                                   GTEX-11NUK-2926-SM-5A5MD  \
Brain - Cortex_ENSG00000187634.11                 -0.066278   
Brain - Cortex_ENSG00000188976.10                  0.033137   
Brain - Cortex_ENSG00000187961.13                 -0.145010   
Brain - Cortex_ENSG00000187583.10                 -0.011115   
Brain - Cortex_ENSG00000187642.9                   0.043859   

                                   GTEX-11O72-2926-SM-5BC4V  \
Brain - Cortex_ENSG00000187634.11                  0.181506   
Brain - Cortex_ENSG00000188976.10                  0.036487   
Brain - Cortex_ENSG00000187961.13                  0.078290   
Brain - Cortex_ENSG00000187583.10                 -0.068303   
Brain - Cortex_ENSG00000187642.9                  -0.025537   

                                   GTEX-11PRG-2926-SM-5987A  \
Brain - Cortex_ENSG00000187634.11                 -0.155149   
Brain - Cortex_ENSG00000188976.10                  0.050835   
Brain - Cortex_ENSG00000187961.13                 -0.161936   
Brain - Cortex_ENSG00000187583.10                  0.203230   
Brain - Cortex_ENSG00000187642.9                   0.159873   

                                   GTEX-11WQK-3026-SM-5EQL6  \
Brain - Cortex_ENSG00000187634.11                  0.368992   
Brain - Cortex_ENSG00000188976.10                 -0.146515   
Brain - Cortex_ENSG00000187961.13                 -0.117322   
Brain - Cortex_ENSG00000187583.10                 -0.098294   
Brain - Cortex_ENSG00000187642.9                   0.197115   

                                   GTEX-11ZUS-2926-SM-5FQSL  \
Brain - Cortex_ENSG00000187634.11                  0.136117   
Brain - Cortex_ENSG00000188976.10                  0.122047   
Brain - Cortex_ENSG00000187961.13                  0.103604   
Brain - Cortex_ENSG00000187583.10                 -0.052249   
Brain - Cortex_ENSG00000187642.9                  -0.141553   

                                   GTEX-12126-1026-SM-5P9JJ  ...  \
Brain - Cortex_ENSG00000187634.11                  0.011542  ...   
Brain - Cortex_ENSG00000188976.10                  0.107677  ...   
Brain - Cortex_ENSG00000187961.13                 -0.153550  ...   
Brain - Cortex_ENSG00000187583.10                 -0.056412  ...   
Brain - Cortex_ENSG00000187642.9                   0.024519  ...   

                                   GTEX-ZDXO-2426-SM-5S2NJ  \
Brain - Cortex_ENSG00000187634.11                      NaN   
Brain - Cortex_ENSG00000188976.10                      NaN   
Brain - Cortex_ENSG00000187961.13                      NaN   
Brain - Cortex_ENSG00000187583.10                      NaN   
Brain - Cortex_ENSG00000187642.9                       NaN   

                                   GTEX-ZE9C-2826-SM-5S2MO  \
Brain - Cortex_ENSG00000187634.11                      NaN   
Brain - Cortex_ENSG00000188976.10            

In [78]:
network_analyser = NetworkAnalysis()
network_analyser.set_analysis_type(analysis_type='inter_tissue')

Initialized inter-tissue network analysis


In [ ]:
inter_tissue_results = network_analyser.load_tissue_data_for_inter_tissue_analysis(
    all_processed_data_clean,
    t

In [1]:
from new_script.network_analysis import NetworkAnalysis

network_analysis = NetworkAnalysis()
network_analysis.set_analysis_type(analysis_type='inter_tissue')

tissue_gene_sets = {}

for tissue, tissue_data in tissue_processed_data.items():
    genes_without_prefix = set([gene.split('_', 1)[1] for gene in tissue_data.index])
    tissue_gene_sets[tissue] = genes_without_prefix
    rprint(f"Tissue: {tissue}, Genes: {len(genes_without_prefix)}")

common_genes = set.intersection(*tissue_gene_sets.values())
common_genes = list(common_genes)
rprint(f"Common genes across all tissues: {len(common_genes)}")

rprint("=== Preparing Data for Inter-Tissue Network Analysis ===")

tissue_expression_data = {}
tissue_sample_mapping = {}

for tissue in target_tissues:
    rprint(f"Processing tissue: {tissue}")
    
    tissue_data = tissue_processed_data[tissue]
    common_tissue_genes = [f"{tissue}_{gene}" for gene in common_genes if f"{tissue}_{gene}" in tissue_data.index]
    tissue_subset = tissue_data.loc[common_tissue_genes]

    tissue_expression_data[tissue] = tissue_subset

    tissue_sample_mapping[tissue] = tissue_young_samples[tissue] + tissue_old_samples[tissue]

network_analysis.load_tissue_data_for_inter_tissue_analysis(
    tissue_expression_data,
    tissue_sample_mapping
)

inter_tissue_results = network_analysis.construct_inter_tissue_network(
    ts_power=6,
    ct_power=3,
    correlation_method='pearson',
    min_module_size=30
)


Initialized inter-tissue network analysis


NameError: name 'tissue_processed_data' is not defined

In [15]:

from new_script.network_analysis import NetworkAnalysis

network_analysis = NetworkAnalysis()
network_analysis.set_analysis_type(analysis_type='inter_tissue')

print("=== Finding Common Genes Across Tissues ===")

# Get all gene sets from each tissue (without tissue prefixes) - CORRECTED LOGIC
tissue_gene_sets = {}
for tissue, tissue_data in tissue_processed_data.items():
    # Remove tissue prefix to get just the gene IDs
    genes_without_prefix = set([gene.split('_', 1)[1] for gene in tissue_data.index])
    tissue_gene_sets[tissue] = genes_without_prefix
    rprint(f"{tissue}: {len(genes_without_prefix)} genes")

# Find intersection of all tissue gene sets
common_genes = set.intersection(*tissue_gene_sets.values())
common_genes = list(common_genes)
rprint(f"Common genes across all tissues: {len(common_genes)}")

print("=== Preparing Data for Inter-Tissue Network ===")

tissue_expression_data = {}
tissue_sample_mapping = {}

for tissue in target_tissues:
    rprint(f"Processing tissue: {tissue}")
    
    tissue_data = tissue_processed_data[tissue]
    common_tissue_genes = [f"{tissue}_{gene}" for gene in common_genes if f"{tissue}_{gene}" in tissue_data.index]
    
    # Get the subset of data with common genes
    tissue_subset = tissue_data.loc[common_tissue_genes]
    rprint(f"  Before transpose: {tissue_subset.shape} (genes × samples)")
    
    # CRITICAL FIX: Transpose to samples × genes format for inter-tissue analysis
    # The inter-tissue network code expects: rows = samples, columns = genes
    tissue_expression_data[tissue] = tissue_subset.T  # Transpose: genes×samples -> samples×genes
    
    # Remove the tissue prefix from gene names for the columns
    tissue_expression_data[tissue].columns = [gene.split('_', 1)[1] for gene in tissue_expression_data[tissue].columns]

    tissue_sample_mapping[tissue] = tissue_young_samples[tissue] + tissue_old_samples[tissue]
    
    rprint(f"  After transpose: {tissue_expression_data[tissue].shape} (samples × genes)")

print("=== Loading Data into Network Analysis ===")

network_analysis.load_tissue_data_for_inter_tissue_analysis(
    tissue_expression_data,
    tissue_sample_mapping
)

print("=== Constructing Inter-Tissue Network ===")

inter_tissue_results = network_analysis.construct_inter_tissue_network(
    ts_power=6,
    ct_power=3,
    correlation_method='pearson',
    min_module_size=30
)


Initialized inter-tissue network analysis
=== Finding Common Genes Across Tissues ===


Brain - Cortex: 7483 genes

Muscle - Skeletal: 8104 genes

Adipose - Subcutaneous: 5610 genes

Common genes across all tissues: 2444

...

Processing tissue: Adipose - Subcutaneous

Before transpose: (2444, 644) (genes × samples)

After transpose: (644, 2444) (samples × genes)

=== Loading Data into Network Analysis ===
Loading tissue expression data...
Processing Brain - Cortex: (242, 2444)
Processing Muscle - Skeletal: (801, 2444)
Processing Adipose - Subcutaneous: (644, 2444)
Total genes across all tissues: 7332
=== Constructing Inter-Tissue Network ===
Constructing inter-tissue network...
Constructing inter-tissue adjacency matrix...
TS power: 6, CT power: 3
Calculating tissue-specific adjacencies...


ValueError: could not broadcast input array from shape (242,242) into shape (2444,2444)

### rpy2 -tut

In [1]:
import os

os.environ['R_MAX_VSIZE'] = '60Gb'  

In [59]:
import rpy2.robjects as robjects
import pandas as pd
from rpy2.robjects import pandas2ri
from rpy2.robjects.packages import importr
import rpy2.rinterface as rinterface


python(38936) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(38937) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
python(38952) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
/opt/anaconda3/envs/new_base/lib/python3.11/site-packages/rpy2/rinterface/__init__.py:1211: UserWarning: Environment variable "PWD" redefined by R and overriding existing variable. Current: "/", R: "/Users/edeneldar/CoExpression_ReProduction"
  warnings.warn(
python(38980) MallocStackLogging: can't turn off malloc stack logging because it was not enabled.
/opt/anaconda3/envs/new_base/lib/python3.11/site-packages/rpy2/rinterface/__init__.py:1211: UserWarning: Environment variable "R_SESSION_TMPDIR" redefined by R and overriding existing variable. Current: "/var/folders/5g/7gzv8rg14tv7prkqk0v2f3280000gn/T//Rtmpe4AfMf", R: "/var/folders/5g/7gzv8rg14tv7prkqk0v2f3280000gn/T//Rtmpx5MSmd"
  warnings.warn

In [60]:
# Use the modern context manager approach instead of deprecated activate()
from rpy2.robjects import conversion, default_converter
from rpy2.robjects.conversion import localconverter

# Create a converter context that includes pandas conversion
converter = default_converter + pandas2ri.converter

In [61]:
#import from r script
# This assumes you have a script named 'r_script.R' in the same directory
r_script_path = 'old_scripts/CrossTissueClusteringMethods.R'
r_script_path_MDC_Validation = '/Users/edeneldar/CoExpression_ReProduction/old_scripts/Modular Differential Connectivity new.R'
with open(r_script_path, 'r') as r_script_file:
    r_script_content = r_script_file.read()

with open(r_script_path_MDC_Validation, 'r') as r_script_file_MDC:
    r_script_content_MDC = r_script_file_MDC.read()
# Import the R script
robjects.r(r_script_content)
# robjects.r(r_script_content_MDC)

# Now you can use the functions defined in the R script
# For example, if the R script defines a function called 'cross_tissue_clustering',
# you can call it like this:
# with localconverter(converter):
#     result = robjects.r.cross_tissue_clustering(robjects.DataFrame(inter_tissue_results['adjacency_matrix']))

R callback write-console: Loading required package: dynamicTreeCut
  
R callback write-console: Loading required package: fastcluster
  
R callback write-console: 
Attaching package: ‘fastcluster’

  
R callback write-console: The following object is masked from ‘package:stats’:

    hclust

  
R callback write-console: 
  
R callback write-console: 
Attaching package: ‘WGCNA’

  
R callback write-console: The following object is masked from ‘package:stats’:

    cor

  


Allowing multi-threading with up to 8 threads.


In [62]:
tissues = ['Muscle', 'Adipose', 'Brain']

In [63]:
young_tissue_file_names_shaked = ["/Users/edeneldar/CoExpression_ReProduction/old_outputs/Adipose - Subcutaneous_young.csv",
                                  "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Muscle - Skeletal_young.csv",
                                  "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Brain - Cortex_young.csv"]
old_tissue_file_names_shaked = ["/Users/edeneldar/CoExpression_ReProduction/old_outputs/Adipose - Subcutaneous_old.csv",
                                 "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Muscle - Skeletal_old.csv",
                                 "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Brain - Cortex_old.csv"]
young_tissue_file_names = ["old_scripts/outputs/Adipose - Subcutaneous/young_matrix.csv",
                            "old_scripts/outputs/Muscle - Skeletal/young_matrix.csv",
                            "old_scripts/outputs/Brain - Cortex/young_matrix.csv"]
old_tissue_file_names = ["old_scripts/outputs/Adipose - Subcutaneous/old_matrix.csv",
                         "old_scripts/outputs/Muscle - Skeletal/old_matrix.csv",
                         "old_scripts/outputs/Brain - Cortex/old_matrix.csv"]


In [64]:
# Install required R packages if not already installed
# Run this cell if you get errors about missing R packages

r_packages_to_install = """
# Install required packages if not already installed
required_packages <- c("WGCNA", "dynamicTreeCut", "gplots")

for (pkg in required_packages) {
    if (!require(pkg, character.only = TRUE)) {
        if (!requireNamespace("BiocManager", quietly = TRUE)) {
            install.packages("BiocManager")
        }
        if (pkg == "WGCNA") {
            BiocManager::install("WGCNA")
        } else {
            install.packages(pkg)
        }
        library(pkg, character.only = TRUE)
    }
}

print("All required packages are installed and loaded.")
"""

# Execute the R code to install packages
robjects.r(r_packages_to_install)

R callback write-console: Loading required package: gplots
  
R callback write-console: 
Attaching package: ‘gplots’

  
R callback write-console: The following object is masked from ‘package:stats’:

    lowess

  


[1] "All required packages are installed and loaded."


In [ ]:
> res <- XWGCNA_Clusters_autoBeta(
+     tissue_names = c("Adipose","Muscle","Brain"),
+     tissue_expr_file_names = c(
+         "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Adipose - Subcutaneous_old.csv",
+         "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Muscle - Skeletal_old.csv",
+         "/Users/edeneldar/CoExpression_ReProduction/old_outputs/Brain - Cortex_old.csv"
+     ),
+     sd_quantile = 0.0,
+     max_genes_per_tissue = 5000,     # if RAM is tight try 2000–3000
+     min_expr = 0,
+     min_prop = 0.01,
+     auto_beta = FALSE,
+     targetR2 = 0.80,
+     beta_grid = 1:20,
+     minClusterSize = 30,
+     cluster_type_thr = 0.95,
+     out_prefix = "xwgcna_old_oriiginal_run7",
+     save_intermediates = TRUE,
+     plot_heatmap = TRUE
+ )

In [ ]:
# Alternative approach: Call individual R functions step by step
# Use this if the main XWGCNA_Clusters function has issues

print("=== Alternative Step-by-Step Approach ===")

try:
    with localconverter(converter):
        # Step 1: Create adjacency matrix
        print("Step 1: Creating adjacency matrix...")
        robjects.r(r_script_content)
        r_func = robjects.r['XWGCNA_Clusters_autoBeta']
        r_tissue_names = robjects.StrVector(tissues)
        r_file_names = robjects.StrVector(young_tissue_file_names_shaked)
        res = r_func(
            tissue_names=r_tissue_names,
            tissue_expr_file_names=r_file_names,
            sd_quantile=0.0,
            max_genes_per_tissue=5000,  # Adjust based on RAM availability
            min_expr=0,
            min_prop=0.01,
            auto_beta=False,
            targetR2=0.80,
            beta_grid=robjects.IntVector(range(1, 21)),  # Range 1 to 20
            minClusterSize=30,
            cluster_type_thr=0.95,
            out_prefix="xwgcna_young_original_run10",
            save_intermediates=True,
            plot_heatmap=True
        )
        # print(list(res.names))
        
        with localconverter(converter):
            o_clusters_table_df = res.getbyname("clusters_table")
            o_clusters_details_df = res.getbyname("clusters_details")
            o_TS_power = int(res.getbyname("TS_power")[0])
            o_CT_power = int(res.getbyname("CT_power")[0])
            if "beta_info" in list(res.names()):
                beta_info_r = res.getbyname("beta_info")

        print(o_TS_power, o_CT_power)
        print(o_clusters_table_df.shape, o_clusters_details_df.shape)

        # # beta_info (only if auto_beta = TRUE)
        # beta_info = None
        # if "beta_info" in list(res.names):
        #     beta_info_r = res.rx2("beta_info")
        #     if beta_info_r is not rinterface.NULL:
        #         beta_info = {}
        #         for name in beta_info_r.names:
        #             obj = beta_info_r.rx2(name)
        #             # Convert data.frames; leave scalars/vectors as is
        #             with localconverter(converter):
        #                 try:
        #                     beta_info[name] = pandas2ri.rpy2py(obj)
        #                 except Exception:
        #                     beta_info[name] = obj
        #         print("beta_info keys:", beta_info.keys())
    # # Extract elements from the returned R list
    # with localconverter(converter):
    #     clusters_table_df   = pandas2ri.rpy2py(res.rx2("clusters_table"))
    #     clusters_details_df = pandas2ri.rpy2py(res.rx2("clusters_details"))

    # TS_power = int(res.rx2("TS_power")[0])
    # CT_power = int(res.rx2("CT_power")[0])

    # beta_info = None
    # if "beta_info" in list(res.names):
    #     beta_r = res.rx2("beta_info")
    #     if beta_r is not rinterface.NULL:
    #         # Safely convert nested list components if present
    #         with localconverter(converter):
    #             beta_info = {}
    #             for name in beta_r.names:
    #                 obj = beta_r.rx2(name)
    #                 try:
    #                     beta_info[name] = pandas2ri.rpy2py(obj)
    #                 except Exception:
    #                     beta_info[name] = obj

    # print(f"TS_power={TS_power}, CT_power={CT_power}")
    # print("clusters_table_df shape:", clusters_table_df.shape)
    # print("clusters_details_df shape:", clusters_details_df.shape)
    # print("beta_info keys:" if beta_info else "No beta_info (auto_beta=False).")

    #     # # adj_mat = robjects.r.AdjacencyFromExpr(
    #     # #     tissue_names=r_tissue_names,
        # #     tissue_expr_file_names=r_file_names,
        # #     MV_sd_thr=0.5,
        # #     TS_power=6,
        # #     CT_power=3,
        # #     cor_method="pearson"
        # # )
        # print("Adjacency matrix created successfully!")
        
        # # Step 2: Create TOM matrix
        # print("Step 2: Creating TOM matrix...")
        # # tom_mat = robjects.r.Cross_Tissue_TOM(adj_mat)
        # print("TOM matrix created successfully!")
        
        # # Step 3: Create clusters
        # print("Step 3: Creating clusters...")
        # # clusters_table_r = robjects.r.Clusters_Table(tom_mat, minClusterSize=30)
        # # clusters_details_r = robjects.r.Clusters_Details(clusters_table_r, cluster_type_thr=0.95)
        
        # print("Clustering completed successfully!")
        
        # # Convert results
        # # clusters_table_alt = pandas2ri.rpy2py(clusters_table_r)
        # # clusters_details_alt = pandas2ri.rpy2py(clusters_details_r)
        
        # print("Results converted to Python successfully!")
        
except Exception as e:
    print(f"Error in step-by-step approach: {e}")
    print("You may need to install R packages or check data format.")

=== Alternative Step-by-Step Approach ===
Step 1: Creating adjacency matrix...
Allowing multi-threading with up to 8 threads.


R callback write-console: Adjacency: 3 tissues, up to 5000 genes/tissue (sd_quantile=0.00, min_prop=0.01).
  
R callback write-console: [Muscle] kept 5000 genes across 76 samples (76 donors)
  
R callback write-console: [Adipose] kept 5000 genes across 102 samples (102 donors)
  
R callback write-console: [Brain] kept 5000 genes across 55 samples (55 donors)
  
R callback write-console: Computing TOM (this may take a while)...
  
R callback write-console: Computing TOM from adjacency matrix... (old)
  
R callback write-console: Number of genes: 15000; Number of samples: 15000
  
R callback write-console: Processing block 1 to 2000
  
R callback write-console: Processed block 1 to 2000
  
R callback write-console: Processing block 2001 to 4000
  
R callback write-console: Processed block 2001 to 4000
  
R callback write-console: Processing block 4001 to 6000
  
R callback write-console: Processed block 4001 to 6000
  
R callback write-console: Processing block 6001 to 8000
  
R callback

6 3
(8666, 3) (111, 8)


In [11]:
df_y_original = pd.read_csv("xwgcna_young_original_run9_clusters_table.tsv", sep="\t")
df_o_original = pd.read_csv("xwgcna_old_original_run9_clusters_table.tsv", sep="\t")

In [12]:
df_y_original_details = pd.read_csv("xwgcna_young_original_run9_clusters_details.tsv", sep="\t")
df_o_original_details = pd.read_csv("xwgcna_old_original_run9_clusters_details.tsv", sep="\t")

In [14]:
list(res.names())

['clusters_table', 'clusters_details', 'TS_power', 'CT_power']

In [8]:
o_clusters_details_df

Cluster ID Cluster Size Cluster Type       Cluster Tissues Adipose Brain  \
1            1          306           CT  Adipose,Brain,Muscle      66   100   
2            2          290           CT  Adipose,Brain,Muscle      56   139   
3            3          199           CT  Adipose,Brain,Muscle      59    91   
4            4          193           TS  Adipose,Brain,Muscle       1     2   
5            5          187           CT  Adipose,Brain,Muscle       5   175   
..         ...          ...          ...                   ...     ...   ...   
107        107           31           CT        Adipose,Muscle       9     0   
108        108           31           TS                 Brain       0    31   
109        109           30           TS               Adipose      30     0   
110        110           30           TS               Adipose      30     0   
111        111           30           TS               Adipose      30     0   

    Muscle Dominant Tissue  
1      140          Muscle  
2       95           Brain  
3       49           Brain  
4      190          Muscle  
5        7           Brain  
..     ...             ...  
107     22          Muscle  
108      0           Brain  
109      0         Adipose  
110      0         Adipose  
111      0         Adipose  

[111 rows x 8 columns]

In [9]:
y_clusters_details_df

NameError: name 'y_clusters_details_df' is not defined

In [10]:
y_clusters_details_df

NameError: name 'y_clusters_details_df' is not defined

In [19]:
res.getbyname("CT_power")

array([3.])

In [18]:
res._NamedList__list

[<rpy2.robjects.vectors.StrMatrix object at 0x10d48e4d0> [16]
 R classes: ('matrix', 'array')
 [' 1', ' 1', ' 1', ' 1', ..., 'ENSG0000..., 'ENSG0000..., 'ENSG0000..., 'ENSG0000...],
 <rpy2.robjects.vectors.StrMatrix object at 0x1457b4710> [16]
 R classes: ('matrix', 'array')
 ['1', '2', '3', '4', ..., 'Adipose', 'Muscle', 'Muscle', 'Brain'],
 array([6.]),
 array([3.])]

In [16]:
from rich import inspect
inspect(res, all = True)

╭─────────────────────────────────── <class 'rpy2.rlike.container.NamedList'> ────────────────────────────────────╮
│ A mutable sequence for which each item might have a 'name'.                                                     │
│                                                                                                                 │
│ ╭─────────────────────────────────────────────────────────────────────────────────────────────────────────────╮ │
│ │ <rpy2.rlike.container.NamedList object at 0x106364950>                                                      │ │
│ ╰─────────────────────────────────────────────────────────────────────────────────────────────────────────────╯ │
│                                                                                                                 │
│      __annotations__ = {                                                                                        │
│                            '_NamedList__list': typing.List,                                                     │
│                            '_NamedList__names': typing.List[typing.Optional[str]]                               │
│                        }                                                                                        │
│             __dict__ = {                                                                                        │
│                            '_NamedList__list': [                                                                │
│                                <rpy2.robjects.vectors.StrMatrix object at 0x10d48e4d0> [16]                     │
│                        R classes: ('matrix', 'array')                                                           │
│                        [' 1', ' 1', ' 1', ' 1', ..., 'ENSG0000..., 'ENSG0000..., 'ENSG0000..., 'ENSG0000...],   │
│                                <rpy2.robjects.vectors.StrMatrix object at 0x1457b4710> [16]                     │
│                        R classes: ('matrix', 'array')                                                           │
│                        ['1', '2', '3', '4', ..., 'Adipose', 'Muscle', 'Muscle', 'Brain'],                       │
│                                array([6.]),                                                                     │
│                                array([3.])                                                                      │
│                            ],                                                                                   │
│                            '_NamedList__names': [                                                               │
│                                'clusters_table',                                                                │
│                                'clusters_details',                                                              │
│                                'TS_power',                                                                      │
│                                'CT_power'                                                                       │
│                            ]                                                                                    │
│                        }                                                                                        │
│              __doc__ = " A mutable sequence for which each item might have a 'name'.\n\n    This is intended to │
│                        mimic R's lists or pairlists.\n    This structure is like a Python list to which         │
│                        optional\n    names for each element in the list is added.\n\n    This cannot be an      │
│                        ordered dictionnary because the keys (names)\n    are not necessarily unique.\n\n        │
│                        :param seq: an iterable.\n    :param names: optional sequence of names\n    :param tags: │
│                        [deprecated] optional sequence 

In [20]:
list(res.names())

['clusters_table', 'clusters_details', 'TS_power', 'CT_power']

In [27]:
# Rebuild clusters_table_df from R matrix
clusters_table_r = res.getbyname('clusters_table')
clusters_details_r = res.getbyname('clusters_details')

In [28]:
nrows, ncols = [int(x) for x in clusters_table_r.dim]
import numpy as np, pandas as pd

In [29]:
data_ct = np.array(clusters_table_r, dtype=str).reshape((nrows, ncols), order='F')
colnames_ct = list(robjects.r.colnames(clusters_table_r)) or [f"V{i+1}" for i in range(ncols)]
clusters_table_df = pd.DataFrame(data_ct, columns=colnames_ct)

nrows2, ncols2 = [int(x) for x in clusters_details_r.dim]
data_cd = np.array(clusters_details_r, dtype=str).reshape((nrows2, ncols2), order='F')
colnames_cd = list(robjects.r.colnames(clusters_details_r)) or [f"V{i+1}" for i in range(ncols2)]
clusters_details_df = pd.DataFrame(data_cd, columns=colnames_cd)

print(clusters_table_df.shape, clusters_details_df.shape)

(8107, 3) (93, 8)


In [22]:
with localconverter(converter):
    clusters_table_df = pandas2ri.rpy2py(res.getbyname('clusters_table'))

In [26]:
clusters_table_df.shape

(24321,)

In [37]:
import polars as pl
import pandas as pd

In [3]:
old_adipose_output_matrix_jud = pl.read_csv(r"old_outputs/Adipose - Subcutaneous_old.csv")
old_adipose_output_matrix_ed = pl.read_csv(r"old_scripts/outputs/Adipose - Subcutaneous/old_matrix.csv")



In [14]:
for col in old_adipose_output_matrix_ed.columns:
    column = col.split('.')[0]
    old_adipose_output_matrix_ed = old_adipose_output_matrix_ed.rename({col: column})

In [11]:
old_adipose_output_matrix_jud[:5, :10]

shape: (5, 10)
┌───────────┬───────────┬───────────┬───────────┬───┬───────────┬───────────┬───────────┬──────────┐
│ column_0  ┆ ENSG00000 ┆ ENSG00000 ┆ ENSG00000 ┆ … ┆ ENSG00000 ┆ ENSG00000 ┆ ENSG00000 ┆ ENSG0000 │
│ ---       ┆ 284413    ┆ 284308    ┆ 283992    ┆   ┆ 282608    ┆ 281991    ┆ 280789    ┆ 0280670  │
│ str       ┆ ---       ┆ ---       ┆ ---       ┆   ┆ ---       ┆ ---       ┆ ---       ┆ ---      │
│           ┆ f64       ┆ f64       ┆ f64       ┆   ┆ f64       ┆ f64       ┆ f64       ┆ f64      │
╞═══════════╪═══════════╪═══════════╪═══════════╪═══╪═══════════╪═══════════╪═══════════╪══════════╡
│ GTEX-1128 ┆ -0.110103 ┆ -0.757219 ┆ -0.067958 ┆ … ┆ 0.340311  ┆ 0.026438  ┆ -0.800089 ┆ 0.573947 │
│ S         ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ GTEX-11EM ┆ 0.044991  ┆ -0.027819 ┆ -0.562634 ┆ … ┆ 0.437061  ┆ 0.163     ┆ -0.383047 ┆ 0.12178  │
│ C         ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
│ GTEX-11GS ┆ 0.047742  ┆ -0.286519 ┆ -0.192671 ┆ … ┆ -0.198085 ┆ 0.162604  ┆ -0.054714 ┆ -1.72242 │
│ 4         ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 5        │
│ GTEX-11GS ┆ -0.524808 ┆ -0.059677 ┆ -0.922296 ┆ … ┆ 1.315391  ┆ 0.12943   ┆ -0.251479 ┆ -0.44178 │
│ O         ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆ 3        │
│ GTEX-11OF ┆ -0.123673 ┆ 0.772489  ┆ -0.225746 ┆ … ┆ -0.7464   ┆ -0.133567 ┆ 1.214273  ┆ 0.942595 │
│ 3         ┆           ┆           ┆           ┆   ┆           ┆           ┆           ┆          │
└───────────┴───────────┴───────────┴───────────┴───┴───────────┴───────────┴───────────┴──────────┘

In [15]:
old_adipose_output_matrix_ed.columns

['',
 'ENSG00000227232',
 'ENSG00000225972',
 'ENSG00000225630',
 'ENSG00000237973',
 'ENSG00000229344',
 'ENSG00000240409',
 'ENSG00000248527',
 'ENSG00000198744',
 'ENSG00000177757',
 'ENSG00000228794',
 'ENSG00000225880',
 'ENSG00000187634',
 'ENSG00000188976',
 'ENSG00000187961',
 'ENSG00000187583',
 'ENSG00000187642',
 'ENSG00000188290',
 'ENSG00000187608',
 'ENSG00000188157',
 'ENSG00000131591',
 'ENSG00000205231',
 'ENSG00000162571',
 'ENSG00000186891',
 'ENSG00000186827',
 'ENSG00000078808',
 'ENSG00000176022',
 'ENSG00000184163',
 'ENSG00000160087',
 'ENSG00000230415',
 'ENSG00000162572',
 'ENSG00000131584',
 'ENSG00000169972',
 'ENSG00000127054',
 'ENSG00000224051',
 'ENSG00000169962',
 'ENSG00000107404',
 'ENSG00000162576',
 'ENSG00000175756',
 'ENSG00000221978',
 'ENSG00000242485',
 'ENSG00000235098',
 'ENSG00000225285',
 'ENSG00000179403',
 'ENSG00000215915',
 'ENSG00000160072',
 'ENSG00000197785',
 'ENSG00000205090',
 'ENSG00000160075',
 'ENSG00000228594',
 'ENSG000001975

In [17]:
common_samples = set(old_adipose_output_matrix_jud.columns).intersection(set(old_adipose_output_matrix_ed.columns))

for column in old_adipose_output_matrix_jud.columns:
    if  column not in old_adipose_output_matrix_ed.columns:
        print(f"Column '{column}' is missing in the old matrix.")
    else:
        print(f"Column '{column}' exists in both matrices.")

Column '' exists in both matrices.
Column 'ENSG00000284413' exists in both matrices.
Column 'ENSG00000284308' exists in both matrices.
Column 'ENSG00000283992' exists in both matrices.
Column 'ENSG00000283787' exists in both matrices.
Column 'ENSG00000283632' exists in both matrices.
Column 'ENSG00000282608' exists in both matrices.
Column 'ENSG00000281991' exists in both matrices.
Column 'ENSG00000280789' exists in both matrices.
Column 'ENSG00000280670' exists in both matrices.
Column 'ENSG00000280165' exists in both matrices.
Column 'ENSG00000278662' exists in both matrices.
Column 'ENSG00000278619' exists in both matrices.
Column 'ENSG00000278615' exists in both matrices.
Column 'ENSG00000278558' exists in both matrices.
Column 'ENSG00000278540' exists in both matrices.
Column 'ENSG00000278535' exists in both matrices.
Column 'ENSG00000278318' exists in both matrices.
Column 'ENSG00000278224' exists in both matrices.
Column 'ENSG00000278129' exists in both matrices.
Column 'ENSG000

In [21]:
len(list(common_samples))

4863

In [26]:

old_adipose_output_matrix_jud[list(common_samples)[0],list(common_samples)[1]]

shape: (76, 2)
┌────────────┬─────────────────┐
│            ┆ ENSG00000185070 │
│ ---        ┆ ---             │
│ str        ┆ f64             │
╞════════════╪═════════════════╡
│ GTEX-1128S ┆ -0.508018       │
│ GTEX-11EMC ┆ -0.824792       │
│ GTEX-11GS4 ┆ 0.222703        │
│ GTEX-11GSO ┆ -0.668774       │
│ GTEX-11OF3 ┆ 0.564789        │
│ …          ┆ …               │
│ GTEX-XOT4  ┆ 0.249949        │
│ GTEX-YJ89  ┆ -0.181232       │
│ GTEX-ZDTS  ┆ 0.524503        │
│ GTEX-ZDXO  ┆ 0.690764        │
│ GTEX-ZE9C  ┆ -0.482967       │
└────────────┴─────────────────┘

In [28]:
old_adipose_output_matrix_ed[list(common_samples)[0],list(common_samples)[1]].sort(list(common_samples)[0])

shape: (83, 2)
┌──────────────────────────┬─────────────────┐
│                          ┆ ENSG00000185070 │
│ ---                      ┆ ---             │
│ str                      ┆ f64             │
╞══════════════════════════╪═════════════════╡
│ GTEX-111FC-0226-SM-5N9B8 ┆ 4.294185        │
│ GTEX-1128S-2126-SM-5H12U ┆ -1.365395       │
│ GTEX-11EMC-2826-SM-5PNY6 ┆ -1.70037        │
│ GTEX-11GS4-2626-SM-5A5LD ┆ 1.512431        │
│ GTEX-11GSO-2326-SM-5A5LX ┆ -1.895193       │
│ …                        ┆ …               │
│ GTEX-SJXC-0226-SM-2XCDU  ┆ -0.717044       │
│ GTEX-XOT4-0226-SM-4B66Z  ┆ 0.378312        │
│ GTEX-YJ89-0226-SM-4TT3Y  ┆ -1.001577       │
│ GTEX-ZDTS-0226-SM-5HL7Q  ┆ 1.806842        │
│ GTEX-ZDXO-2426-SM-5S2NJ  ┆ 2.273172        │
└──────────────────────────┴─────────────────┘

# review the gtex dataprep

In [1]:
#imports
import pandas as pd
import os 
from pathlib import Path
import re
import copy
import pickle

import numpy as np
import scipy as stats
import random
from rich import print as rprint
from rich.progress import track

import seaborn as sns
import matplotlib.pyplot as plt

import scipy as sp
from scipy.stats import chi2
from sklearn.covariance import MinCovDet

from sklearn.decomposition import PCA
from sklearn.decomposition import TruncatedSVD

from sklearn.linear_model import LinearRegression
from sklearn.feature_selection import f_regression


In [3]:
GTEx_tpm = pd.read_csv('data/GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_tpm.gct', sep='\t',skiprows=2)


: 

In [2]:
GTEx_tpm = pd.read_csv('data/GTEx_Analysis_2017-06-05_v8_RNASeQCv1.1.9_gene_tpm.gct', sep='\t',skiprows=2)
HGNC_list = pd.read_csv('data/hgnc_complete_set.tsv', sep='\t')
pheno_df = pd.read_csv('data/GTEx_Analysis_v8_Annotations_SubjectPhenotypesDS.tsv', sep='\t', index_col=0)
attributes_df = pd.read_csv('data/GTEx_Analysis_v8_Annotations_SampleAttributesDS.tsv', sep='\t', index_col=0)


KeyboardInterrupt: 

# Key genes after filtering

In [8]:
import polars as pl
import pandas as pd
import os

In [10]:
modulesDetailsYoung = pd.read_csv(r"/Users/edeneldar/CoExpression_ReProduction/xwgcna_young_original_run9_Clusters_details.tsv", sep ='\t')
modulesTableYoung = pd.read_csv(r"/Users/edeneldar/CoExpression_ReProduction/xwgcna_young_original_run9_Clusters_table.tsv", sep ='\t')
MDCValidationTest50p = pd.read_csv(r"/Users/edeneldar/CoExpression_ReProduction/DiffConnectvty_young_to_old_new/xwgcna_young_original_run9_Clusters_table_VS_old_MDC_both_p50_wFDR2.xls", sep='\t')
# MDCValidationTest100p = pd.read_csv(r"/Users/edeneldar/CoExpression_ReProduction/DiffConnectvty_young_to_old_new/xwgcna_young_original_run9_Clusters_table_VS_old_MDC_both_p100_wFDR.xls", sep='\t')


In [11]:
modulesTableYoung.columns

Index(['Cluster ID', 'Tissue', 'Gene Symbol'], dtype='object')

In [12]:
modulesDetailsYoung.columns

Index(['Cluster ID', 'Cluster Size', 'Cluster Type', 'Cluster Tissues',
       'Adipose', 'Brain', 'Muscle', 'Dominant Tissue'],
      dtype='object')

In [21]:
GOCModules50p = MDCValidationTest50p[MDCValidationTest50p['MDC'] >= 1.8]
# GOCModules100p = MDCValidationTest100p[MDCValidationTest100p['MDC'] >= 1.8]
MDCModules50p = MDCValidationTest50p[MDCValidationTest50p['FDR_random_genes'] < 0.05]

sigGenesGOCModules50p = GOCModules50p[GOCModules50p['FDR_random_genes'] < 0.05]
# sigGenesGOCModules100p = GOCModules100p[GOCModules100p['FDR_random_genes'] < 0.05]

#sigGOCModules50p = GOCModules50p[GOCModules50p['FDR'] < 0.05]
# sigGOCModules100p = GOCModules100p[GOCModules100p['FDR'] < 0.05]



In [22]:
MDCModules50p

module   MDC    FDR  FDR_random_samples  FDR_random_genes  \
0        1  1.80  0.000               0.000             0.000   
1        2  1.68  0.000               0.000             0.000   
3        4  1.49  0.005               0.000             0.005   
4        5  1.70  0.000               0.000             0.000   
6        7  0.85  1.000               1.000             0.000   
10      11  1.52  0.005               0.000             0.005   
12      13  1.93  0.000               0.000             0.000   
13      14  0.96  1.000               1.000             0.004   
14      15  0.91  1.000               1.000             0.000   
15      16  0.78  0.988               0.988             0.000   
17      18  1.67  0.000               0.000             0.000   
18      19  1.80  0.000               0.000             0.000   
19      20  1.57  0.003               0.000             0.003   
20      21  0.80  0.981               0.981             0.000   
21      22  1.46  0.028               0.000             0.028   
25      26  1.70  0.000               0.000             0.000   
28      29  1.71  0.000               0.000             0.000   
29      30  0.80  0.979               0.979             0.000   
31      32  1.68  0.003               0.000             0.003   
33      34  1.77  0.000               0.000             0.000   
35      36  0.87  0.962               0.962             0.006   
36      37  1.51  0.034               0.000             0.034   
39      40  0.81  0.909               0.909             0.001   
42      43  1.63  0.008               0.000             0.008   
43      44  1.59  0.020               0.000             0.020   
46      47  2.44  0.000               0.000             0.000   
48      49  1.72  0.003               0.000             0.003   
50      51  1.58  0.022               0.000             0.022   
51      52  0.73  0.773               0.773             0.000   
52      53  2.06  0.000               0.000             0.000   
53      54  1.54  0.039               0.000             0.039   
59      60  0.78  0.986               0.986             0.009   
60      61  1.75  0.009               0.000             0.009   
61      62  0.82  0.750               0.750             0.023   
64      65  1.61  0.041               0.000             0.041   
65      66  2.30  0.102               0.102             0.000   
66      67  2.08  0.000               0.000             0.000   
71      72  3.26  0.000               0.000             0.000   
72      73  0.68  0.336               0.336             0.002   
75      76  1.95  0.010               0.000             0.010   
76      77  0.74  0.652               0.652             0.007   
77      78  1.65  0.044               0.000             0.044   
84      85  1.89  0.017               0.000             0.017   
85      86  0.66  0.455               0.455             0.001   

    FDR_normal_random_samples  FDR_normal_random_genes  p_empirical_genes  \
0                0.000000e+00             1.275000e-27           0.000999   
1                0.000000e+00             1.098000e-08           0.000999   
3                0.000000e+00             2.005000e-03           0.005994   
4                0.000000e+00             2.202000e-08           0.000999   
6                1.000000e+00             1.647000e-04           1.000000   
10               4.729000e-87             1.563000e-03           0.005994   
12               0.000000e+00             1.236000e-12           0.000999   
13               1.000000e+00             1.000000e-02           0.996000   
14               1.000000e+00             2.555000e-03           1.000000   
15               9.931000e-01             1.478000e-05           1.000000   
17              6.345000e-179             2.726000e-05           0.000999   
18              1.197000e-239             5.688000e-08           0.000999   
19              6.223000e-229             1.314000e-03           0.003996   


In [19]:
CTmodulesY = modulesDetailsYoung[(modulesDetailsYoung['Cluster Type'] == 'CT') & (modulesDetailsYoung['Cluster Size'] >= 50)]
CTmodules = CTmodulesY['Cluster ID']


In [23]:
keyCTModulesp50 = sigGenesGOCModules50p[sigGenesGOCModules50p['module'].isin(CTmodules)]['module']
# keyCTModulesp100 = sigGOCModules100p[sigGOCModules100p['module'].isin(CTmodules)]['Cluster ID']



In [24]:
keyCTModulesp50

0      1
12    13
46    47
65    66
Name: module, dtype: int64

In [25]:
modulesTableYoung.columns

Index(['Cluster ID', 'Tissue', 'Gene Symbol'], dtype='object')

In [27]:
modulesDetailsYoungFDRMDC = pd.merge(modulesDetailsYoung, MDCValidationTest50p, left_on='Cluster ID', right_on='module', how='left')

In [31]:
modulesDetailsYoungFDRMDC['isGOC'] = modulesDetailsYoungFDRMDC['MDC'] > 1
modulesDetailsYoungFDRMDC = modulesDetailsYoungFDRMDC[['Cluster ID', 'Cluster Size', 'Cluster Type', 'Cluster Tissues', 'Adipose', 'Brain', 'Muscle', 'MDC', 'FDR_random_genes', 'FDR_random_samples','isGOC']]
modulesDetailsYoungFDRMDC.to_csv('modulesDetailsYoungFDRMDC.csv', index=False)

In [26]:
keyGOCgenes = modulesTableYoung[modulesTableYoung['Cluster ID'].isin(keyCTModulesp50)]['Gene Symbol']
len(keyGOCgenes)

1003

In [1]:
import pandas as pd

In [2]:
shakeds_cluster_MDC_res = pd.read_csv(r'/Users/edeneldar/CoExpression_ReProduction/cluster_merged_young.csv')
shakeds_cluster_MDC_res.columns

Index(['Cluster ID', 'Cluster Size', 'Cluster Type', 'Cluster Tissues',
       'Adipose', 'Brain', 'Muscle', 'Dominant Tissue', 'MDC', 'FDR',
       'Description'],
      dtype='object')

In [3]:
Eden_cluster_MDC_res = pd.read_csv(r'/Users/edeneldar/CoExpression_ReProduction/DiffConnectvty_young_to_old_new/xwgcna_young_original_run9_Clusters_table_VS_old_MDC_both_p100_wFDR.xls',sep='\t')
Eden_cluster_MDC_res.columns

Index(['module', 'MDC', 'FDR', 'FDR_random_samples', 'FDR_random_genes',
       'p_empirical_genes', 'p_empirical_samples'],
      dtype='object')

In [4]:
merged_df = pd.merge(
    shakeds_cluster_MDC_res,
    Eden_cluster_MDC_res,
    left_on='Cluster ID',
    right_on='module',
    suffixes=('_shaked', '_eden')
)
merged_df.columns

Index(['Cluster ID', 'Cluster Size', 'Cluster Type', 'Cluster Tissues',
       'Adipose', 'Brain', 'Muscle', 'Dominant Tissue', 'MDC_shaked',
       'FDR_shaked', 'Description', 'module', 'MDC_eden', 'FDR_eden',
       'FDR_random_samples', 'FDR_random_genes', 'p_empirical_genes',
       'p_empirical_samples'],
      dtype='object')

In [5]:
merged_df = merged_df[['Cluster ID', 'MDC_shaked', 'FDR_shaked', 'MDC_eden', 'FDR_random_genes']]
merged_df

Cluster ID  MDC_shaked  FDR_shaked  MDC_eden  FDR_random_genes
0            1        1.80        0.00    1.7984              0.00
1            2        1.68        0.00    1.6772              0.00
2            3        1.22        0.40    1.2193              0.39
3            4        1.49        0.00    1.4867              0.00
4            5        1.70        0.00    1.7019              0.00
..         ...         ...         ...       ...               ...
85          86        0.66        0.00    0.6612              0.02
86          87        1.22        0.50    1.2194              0.42
87          88        1.72        0.04    1.7168              0.04
88          89        0.99        0.18    0.9882              0.29
89          90        1.18        0.54    1.1824              0.38

[90 rows x 5 columns]

In [6]:
# Calculate diffModules - modules that gave FDR < 0.05 only for Eden XOR only for Shaked
diffModules = merged_df[(merged_df['FDR_shaked'] < 0.05) ^ (merged_df['FDR_random_genes'] < 0.05)]

In [7]:
diffModules

Cluster ID  MDC_shaked  FDR_shaked  MDC_eden  FDR_random_genes
44          45        0.98        0.06    0.9791              0.02
49          50        0.98        0.02    0.9770              0.06
53          54        1.54        0.02    1.5423              0.05
64          65        1.61        0.08    1.6060              0.04
77          78        1.65        0.06    1.6515              0.03
80          81        1.62        0.08    1.6243              0.04

In [47]:
kegg_enriched_table_y = pd.read_csv(r"/Users/edeneldar/CoExpression_ReProduction/kegg_young.csv")
go_enriched_table_y = pd.read_csv(r"/Users/edeneldar/CoExpression_ReProduction/go_bp_tab_young.csv")

ParserError: Error tokenizing data. C error: Expected 15 fields in line 4, saw 17


In [33]:
kegg_enriched_table_y.columns

Index(['Cluster', 'Cluster.ID', 'category', 'subcategory', 'ID', 'Description',
       'GeneRatio', 'BgRatio', 'RichFactor', 'FoldEnrichment', 'zScore',
       'pvalue', 'p.adjust', 'qvalue', 'geneID', 'Count'],
      dtype='object')

In [55]:
# Aggregate the kegg_enriched_table_y df by min of p.adjust column group by Cluster.ID and Cluster
kegg_enriched_table_y_agg = kegg_enriched_table_y.groupby(['Cluster', 'ID']).agg({'p.adjust': 'min'}).reset_index()


In [54]:
kegg_enriched_table_y_agg

Cluster.ID  Cluster                                  ID  \
0      Cellular Processes        1                   Adherens junction   
1      Cellular Processes        1                           Apoptosis   
2      Cellular Processes        1        Apoptosis - multiple species   
3      Cellular Processes        1                  Autophagy - animal   
4      Cellular Processes        1                   Autophagy - other   
...                   ...      ...                                 ...   
11172  Organismal Systems       90                       Axon guidance   
11173  Organismal Systems       90         Chemokine signaling pathway   
11174  Organismal Systems       90                   Insulin secretion   
11175  Organismal Systems       90      Neurotrophin signaling pathway   
11176  Organismal Systems       90  Vascular smooth muscle contraction   

       p.adjust  
0      0.673492  
1      0.075162  
2      0.686736  
3      0.750657  
4      0.686736  
...         ...  
11172  0.161162  
11173  0.161162  
11174  0.149917  
11175  0.158627  
11176  0.004186  

[11177 rows x 4 columns]

In [58]:
kegg_enriched_table_y_agg.loc[kegg_enriched_table_y_agg['Cluster'] == 47]

Cluster                                                 ID  p.adjust
7766       47  AGE-RAGE signaling pathway in diabetic complic...  0.166317
7767       47                             Acute myeloid leukemia  0.121222
7768       47                                  Adherens junction  0.166317
7769       47                    Adipocytokine signaling pathway  0.360545
7770       47                            African trypanosomiasis  0.001999
...       ...                                                ...       ...
7903       47                                 Yersinia infection  0.423748
7904       47                         cGMP-PKG signaling pathway  0.442767
7905       47                                           hsa03018  0.482717
7906       47                                           hsa04120  0.549650
7907       47                              p53 signaling pathway  0.045303

[142 rows x 3 columns]

In [56]:
# Keep for each Cluster only one Cluster.ID by the min p.adjust
kegg_enriched_table_y_agg_main_proc = kegg_enriched_table_y_agg.loc[kegg_enriched_table_y_agg.groupby('Cluster')['p.adjust'].idxmin()]

In [57]:
kegg_enriched_table_y_agg_main_proc

Cluster                                      ID  p.adjust
47           1                       Carbon metabolism  0.000116
355          2                       Cocaine addiction  0.242141
636          3                                 Glycine  0.255500
825          4     Complement and coagulation cascades  0.425550
1000         5                       Carbon metabolism  0.143801
...        ...                                     ...       ...
11196       86                           Efferocytosis  0.020612
11223       87  Adrenergic signaling in cardiomyocytes  0.169209
11298       88         Arginine and proline metabolism  0.030900
11320       89                               Apoptosis  0.089031
11373       90      Vascular smooth muscle contraction  0.004186

[90 rows x 3 columns]

In [44]:
modulesDetailsYoungFDRMDC_enriched = pd.merge(
    modulesDetailsYoungFDRMDC,
    kegg_enriched_table_y_agg_main_proc[['Cluster', 'Cluster.ID', 'p.adjust']],
    left_on='Cluster ID',
    right_on='Cluster',
    suffixes=('_main', '_sub')
)


In [46]:
modulesDetailsYoungFDRMDC_enriched.to_csv('modulesDetailsYoungFDRMDC_enriched.csv', index=False)